In [95]:

import json
import unicodedata
import numpy as np
import networkx as nx
import requests
from pattern import web
import matplotlib.pyplot as plt

# set some nicer defaults for matplotlib
from matplotlib import rcParams

def get_poll_xml1(poll_id):
    url = "http://www.nhl.com/scores/htmlreports/20142015/GS0%i.HTM" % int(poll_id)
    return requests.get(url).text

from bs4 import BeautifulSoup
Scorers=[]
FstAssistsPlayers=[]
SndAssistsPlayers=[]
plusMinusPlayers=[]
# [20036,20461,20846,21114,21151,21164,21176]:
# [20036,20149,20235,20332,20461,20742,20846,21114,21151,21164,21176]:
for numGames in range(20001,21231):
    if numGames not in [20036,20078,20149,20232,20235,20290,20332,20441,20461,20547,20742,20755,20812,20846,20903,21025,21114,21144,21151,21164,21176]:
        print numGames
        soup = BeautifulSoup(get_poll_xml1(numGames))
        # soup

        result1= soup.find_all("tr", attrs={"class":"oddColor"} )
#         resultCenter= soup.find_all("td", attrs={"align":"center","class":"oddColor"} )
#         resultCen= result1.find_all("td", attrs={"align":"center"} )
        resultCen=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1]
#         print resultCen
        
        result2=[elem.find_all("td", attrs={"align":"left"} ) for elem in result1]

        resultEven= soup.find_all("tr", attrs={"class":"evenColor"} )

        resultEven=[elem.find_all("td", attrs={"align":"left"} ) for elem in resultEven]

        result3= soup.find_all("td", attrs={"align":"center", "style":"font-size: 40px;font-weight:bold"} )

        totalGoals=sum([int(elem.text.strip()) for elem in result3])

        if totalGoals%2==0:
            ODDGoals=totalGoals/2
            EVENGoals=totalGoals/2
        else:
            ODDGoals=totalGoals/2+1
            EVENGoals=totalGoals/2

        oddGoals=[]
        oddFstAssists=[]
        oddSndAssists=[]
        oddarrayFailure=[]
        for x in range(0,ODDGoals):
            if len(result2[x])==3:
                oddGoals.append(result2[x][0])
                oddFstAssists.append(result2[x][1])
                oddSndAssists.append(result2[x][2])
            else:
                oddarrayFailure.append(x)

        evenGoals=[]
        evenFstAssists=[]
        evenSndAssists=[]    
        evenarrayFailure=[]
        for x in range(0,EVENGoals):
        #     print "Test"
        #     print 
            if len(resultEven[x])==3:
                evenGoals.append(resultEven[x][0])
        #         print resultEven[x][1]
                evenFstAssists.append(resultEven[x][1])
                evenSndAssists.append(resultEven[x][2])
            else:
                evenarrayFailure.append(x)
        #     else:
        #         evenGoals.append(resultEven[x][0])
        # #         print resultEven[x][1]
        #         evenFstAssists.append(resultEven[x][1])
        #         evenSndAssists.append()



        resultplayers=soup.find_all("font", attrs={"style":"cursor:hand;"} )

        tds=soup.find_all("td" )[1:]
        tds=[str(elem) for elem in tds]

        count=[]
        tds2=[]
    #     print tds

        for x in range(0,len(tds)):
            if "font style=" in tds[x]:
                count.append(tds[x].count ("font style="))
                tds2.append(tds[x])
    #     print tds2[2]
    #     print tds2
        if tds2!=[]:
            indices = [i for i, x in enumerate(tds2[2]) if x == ","]
        #     print tds2[2]
            temp=[]
            for x in range(0,len(indices)):
                if x==0:
                    temp.append(tds2[2][:indices[0]])
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x!=len(indices)-1:
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x==len(indices)-1:
                    temp.append(tds2[2][indices[x]:len(tds2[2])])
    #         print temp
            if temp!=[]:
                temp[0]=temp[0].replace("<td>", "")
        #     print temp

        #     print temp
            for x in range(0,len(temp)):
                temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                temp[x]=temp[x][0:(temp[x].index("<"))] 
            arrayTemp=[]

            indices = []

            arrayTemp=[]
            for y in range(1,len(tds2)):
                temp=[]
                indices = [i for i, x in enumerate(tds2[y]) if x == ","]
            #     print tds2[y]
            #     print indices
                for x in range(0,len(indices)):
                    if x==0:
                        temp.append(tds2[y][:indices[0]])
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x!=len(indices)-1:
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x==len(indices)-1:
                        temp.append(tds2[y][indices[x]:len(tds2[y])])
        #         print y
        #         print temp
                if temp!=[]:
                    temp[0]=temp[0].replace("<td>", "")
            #     print y
            #     print temp
                for x in range(0,len(temp)):
                    temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                    temp[x]=temp[x][0:(temp[x].index("<"))]
                arrayTemp.append(temp)



            resultTeam=[elem.find_all("td", attrs={"align":"left","class":"heading + bborder"} ) for elem in soup]
            homeTeam=resultTeam[0][3].text.strip()[:resultTeam[0][3].text.strip().index(" ")]
            awayTeam=resultTeam[0][4].text.strip()[:resultTeam[0][4].text.strip().index(" ")]
            resultTeam1= soup.find_all("tr", attrs={"class":"oddColor"} )
            resultTeam2=[elem.find_all("td", attrs={"align":"center"} ) for elem in resultTeam1]

            result1TeamEven= soup.find_all("tr", attrs={"class":"evenColor"} )
            result2TeamEven=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1TeamEven]
            oddGoalTeam=[]
            evenGoalTeam=[]
        #     print "EVENGoals"
        #     print ODDGoals
        #     print EVENGoals
        #     print arrayTemp
#             print "evenarrayFailure"
#             print evenarrayFailure
        #     # oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
        #     # print indicesloc

        #     print arrayTemp
    #         print 
            for x in range(0,ODDGoals):
                if x  not in oddarrayFailure:
                    oddGoalTeam.append(str(resultTeam2[x][4].text.strip()))
#             print evenarrayFailure
            for x in range(0,EVENGoals):
        #         print x
                if x not in evenarrayFailure:
        #             print x
                    evenGoalTeam.append(str(result2TeamEven[x][4].text.strip()))

            indicesloc = [i for i, x in enumerate(arrayTemp) if x == []]
            # print arrayTemp.index([])
        #     print indicesloc 
            # indicesloc=[]
            indicesloc= [ elem/2  for elem in indicesloc if elem%2==0]
        #     print "result2TeamEven[indicesloc[0]]"
        #     print indicesloc
        #     print result2TeamEven[0]
        #     print result2TeamEven[1]
        #     print result2TeamEven[2]
        #     print result2TeamEven[3]
        #     print result2TeamEven[4]
        #     print result2TeamEven[5]
        #     print "result2TeamEven[indicesloc[0]/2]"
            # print result2TeamEven[indicesloc[0]/2]

            # print result2TeamEven
    #         print indicesloc
    #         print totalGoals
            # print result2TeamEven[indicesloc[0]]
    #         print evenGoalTeam
#             print "result2[0]"
#             print result2[0]
#             print result2[1]
#             print result2[2]
            
            totalGoals1=totalGoals
            for x in range(0,len(indicesloc)):
    #             print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                totalGoals1=totalGoals1+1
                if totalGoals%2==0:
                    print "Even!"
                    oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals  and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
                    print "Odd!"
    #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
                    evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #         print indicesloc
    #         print totalGoals
    #         print evenGoalTeam
            if totalGoals%2==0:
                ODDGoals1=totalGoals1/2
                EVENGoals1=totalGoals1/2
            else:
                ODDGoals1=totalGoals1/2+1
                EVENGoals1=totalGoals1/2
#             print "resultCen[totalGoals1]"
#             print resultCen[EVENGoals1][2]
#             print resultCen[ODDGoals1][2]
#             print resultCen[EVENGoals1][1]
#             print resultCen[ODDGoals1][1]
#             print resultCen[EVENGoals1][0]
            resultCenEVENGoals1=str(resultCen[EVENGoals1][1])
#             print resultCenEVENGoals1[(resultCenEVENGoals1.index(">")+1):len(resultCenEVENGoals1)]
#             print str(resultCen[EVENGoals1][1])
#             print str(resultCen[EVENGoals1][1])[(str(resultCen[EVENGoals1][1]).index(">")+1):]
            if totalGoals1%2==1:
                strtemp=str(resultCen[EVENGoals1][1])[(str(resultCen[EVENGoals1][1]).index(">"))+1:]
                strtemp=strtemp[0:(strtemp.index("<"))] 
            else:
                strtemp=str(resultCen[ODDGoals1][1])[(str(resultCen[ODDGoals1][1]).index(">"))+1:]
                strtemp=strtemp[0:(strtemp.index("<"))]
#             print strtemp
            
#         <td align="center">SO</td>
#             temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
#                 temp[x]=temp[x][0:(temp[x].index("<"))] 

#             print resultCen[ODDGoals1][0]
            
                
    #         [1]
    # 3
    # []
            oddArrayTemp=[]
            evenArrayTemp=[]
            for y in range(0,len(arrayTemp)):
                if y%4==1:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==0:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==2:
                    evenArrayTemp.append(arrayTemp[y]) 
                elif y%4==3:
                    evenArrayTemp.append(arrayTemp[y])
        #     print "oddArrayTemp"   
            # print arrayTemp.index([])

        #     print oddGoalTeam
        #     print evenGoalTeam
        #     print oddArrayTemp
        #     for y in range(0,len(oddArrayTemp)/2):
        #         if oddGoalTeam[y]==homeTeam:
        #             oddArrayTemp[2*y].append("W")
        #             oddArrayTemp[2*y+1].append("L")
        #         else:
        #             oddArrayTemp[2*y].append("L")
        #             oddArrayTemp[2*y+1].append("W")

        #     print evenArrayTemp
        #     print evenGoalTeam
        #     print evenarrayFailure
        #     print len(evenArrayTemp)
        #     print arrayTemp
        #     print len(evenArrayTemp)/2
        #     print len(evenGoalTeam)
        #     print evenGoalTeam
            evenArrayTemp=filter(lambda a: a != [], evenArrayTemp)
            oddArrayTemp=filter(lambda a: a != [], oddArrayTemp)
            # evenArrayTemp.remove([])
        #     print evenArrayTemp
    #         print oddGoalTeam
    #         print oddArrayTemp
    #         print evenGoalTeam
    #         print evenArrayTemp
            for y in range(0,len(oddArrayTemp)/2):
                if oddGoalTeam[y]==homeTeam:
                    oddArrayTemp[2*y].insert(0,"W")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"L")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    oddArrayTemp[2*y].insert(0,"L")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"W")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
    #         print evenArrayTemp
    #         print evenGoalTeam

            for y in range(0,len(evenArrayTemp)/2):
                if evenGoalTeam[y]==homeTeam:
                    evenArrayTemp[2*y].insert(0,"W")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"L")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    evenArrayTemp[2*y].insert(0,"L")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"W")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)

        #     for y in range(0,len(evenArrayTemp)/2):
        #     #     print y
        #         if evenGoalTeam[y]==homeTeam:
        #             evenArrayTemp[2*y].append("W")
        #             evenArrayTemp[2*y+1].append("L")
        #         else:
        #             evenArrayTemp[2*y].append("L")
        #             evenArrayTemp[2*y+1].append("W")

        #     print 
        #     print result2[1]
        #     print result2[2]
        #     print result2[3]
        #     print indicesloc
    #         print totalGoals
    #         print indicesloc
            for x in range(0,len(indicesloc)):
            #     print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0:
            #         evenGoalTeam.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
    #                 evenGoals.append(result2[EVENGoals][0])
    #                 evenFstAssists.append(result2[EVENGoals][1])
    #                 evenSndAssists.append(result2[EVENGoals][2])
                    if len(result2[ODDGoals])==3:
                        oddGoals.append(result2[ODDGoals][0])
                        oddFstAssists.append(result2[ODDGoals][1])
                        oddSndAssists.append(result2[ODDGoals][2])
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
            #         oddGoalTeam.append((str(resultTeam2[indicesloc[x]][4].text.strip())))
    #                 oddGoals.append(result2[ODDGoals][0])
    #                 oddFstAssists.append(result2[ODDGoals][1])
    #                 oddSndAssists.append(result2[ODDGoals][2])
#                     print resultEven
                    if len(resultEven[EVENGoals])==3:
                        evenGoals.append(resultEven[EVENGoals][0])
                        evenFstAssists.append(resultEven[EVENGoals][1])
                        evenSndAssists.append(resultEven[EVENGoals][2])

            # oddGoals.append(result2[ODDGoals][0])
            # oddFstAssists.append(result2[ODDGoals][1])
            # oddSndAssists.append(result2[ODDGoals][2])

            oddGoalsNumber= [str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddGoals]
            oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
            oddSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddSndAssists]
            evenGoalsNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenGoals]
            evenFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenFstAssists]
            evenSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenSndAssists ]
        #     print "evenGoalsNumber"
        #     print oddGoals
            # for x in range(0,len(indicesloc)):
            #     print x
            #     if indicesloc[x]%2==0:
            #         evenGoalsNumber.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
            #     else:
            #         oddGoalsNumber.append((str(resultTeam2[indicesloc[x]][4].text.strip())))

            goalOdd = []
            fstAssistOdd = []
            sndAssistOdd = []

            for y in range(0,len(oddGoalTeam)):
                goalOdd.append([])
                fstAssistOdd.append([])
                sndAssistOdd.append([])
        #     print oddGoalsNumber
        #     print oddFstNumber
        #     print oddSndNumber
        #     print oddGoalTeam
            for y in range(0,len(oddGoalTeam)):
                goalOdd[y].append(oddGoalsNumber[y])
                fstAssistOdd[y].append(oddFstNumber[y])
                sndAssistOdd[y].append(oddSndNumber[y])

            goalEven = []
            fstAssistEven = []
            sndAssistEven = []

            for y in range(0,len(evenGoalTeam)):
                goalEven.append([])
                fstAssistEven.append([])
                sndAssistEven.append([])

#             print evenGoalsNumber
        #     print evenFstNumber
        #     print evenSndNumber
#             print evenGoalTeam
        #     print evenarrayFailure
        
            for y in range(0,len(evenGoalTeam)):
                goalEven[y].append(evenGoalsNumber[y])
                fstAssistEven[y].append(evenFstNumber[y])
                sndAssistEven[y].append(evenSndNumber[y])


            for y in range(0,len(goalEven)):
                if evenGoalTeam[y]==homeTeam:
                    goalEven[y].insert(0,str(homeTeam))
                    fstAssistEven[y].insert(0,str(homeTeam))
                    sndAssistEven[y].insert(0,str(homeTeam))
                else:
                    goalEven[y].insert(0,str(awayTeam))
                    fstAssistEven[y].insert(0,str(awayTeam))
                    sndAssistEven[y].insert(0,str(awayTeam))

        #     print "goalEven"
        #     print goalEven
        #     print fstAssistEven
        #     print sndAssistEven
    #         print oddGoalTeam
    #         print goalOdd
            for y in range(0,len(goalOdd)):
                if oddGoalTeam[y]==homeTeam:
                    goalOdd[y].insert(0,str(homeTeam))
                    fstAssistOdd[y].insert(0,str(homeTeam))
                    sndAssistOdd[y].insert(0,str(homeTeam))
                else:
                    goalOdd[y].insert(0,str(awayTeam))
                    fstAssistOdd[y].insert(0,str(awayTeam))
                    sndAssistOdd[y].insert(0,str(awayTeam))

        #     print "goalOdd"
        #     print goalOdd
        #     print fstAssistOdd
        #     print sndAssistOdd



        #     print goalEven+goalOdd
        #     print fstAssistEven+fstAssistOdd
        #     print sndAssistEven+sndAssistOdd
#             print "evenArrayTemp+oddArrayTemp"
#             print evenArrayTemp+oddArrayTemp
            Goal=goalEven+goalOdd
            FstAssist=fstAssistEven+fstAssistOdd
            SndAssist=sndAssistEven+sndAssistOdd
            ArrayTemp=evenArrayTemp+oddArrayTemp
            
            if strtemp=="SO":
                del ArrayTemp[-1]
                del FstAssist[-1]
                del SndAssist[-1]
                del Goal[-1]
            Scorers.append(Goal)
            FstAssistsPlayers.append(FstAssist)
            SndAssistsPlayers.append(SndAssist)
            plusMinusPlayers.append(ArrayTemp)
#     elif numGames in [20149,20235,20332,20742]:
    elif numGames in [20149,20332,20742]:
        # [20036,20149,20235,20332,20461,20742,20846,21114,21151,21164,21176]:
#             [20149,20235,20332,20742]:
        print numGames
        soup = BeautifulSoup(get_poll_xml1(numGames))
        # soup

        result1= soup.find_all("tr", attrs={"class":"oddColor"} )

        result2=[elem.find_all("td", attrs={"align":"left"} ) for elem in result1]

        resultEven= soup.find_all("tr", attrs={"class":"evenColor"} )

        resultEven=[elem.find_all("td", attrs={"align":"left"} ) for elem in resultEven]

        result3= soup.find_all("td", attrs={"align":"center", "style":"font-size: 40px;font-weight:bold"} )

        totalGoals=sum([int(elem.text.strip()) for elem in result3])

        if totalGoals%2==0:
            ODDGoals=totalGoals/2
            EVENGoals=totalGoals/2
        else:
            ODDGoals=totalGoals/2+1
            EVENGoals=totalGoals/2

        oddGoals=[]
        oddFstAssists=[]
        oddSndAssists=[]
        oddarrayFailure=[]
        for x in range(0,ODDGoals):
            if len(result2[x])==3:
                oddGoals.append(result2[x][0])
                oddFstAssists.append(result2[x][1])
                oddSndAssists.append(result2[x][2])
            else:
                oddarrayFailure.append(x)

        evenGoals=[]
        evenFstAssists=[]
        evenSndAssists=[]    
        evenarrayFailure=[]
        for x in range(0,EVENGoals):
        #     print "Test"
        #     print 
            if len(resultEven[x])==3:
                evenGoals.append(resultEven[x][0])
        #         print resultEven[x][1]
                evenFstAssists.append(resultEven[x][1])
                evenSndAssists.append(resultEven[x][2])
            else:
                evenarrayFailure.append(x)
        #     else:
        #         evenGoals.append(resultEven[x][0])
        # #         print resultEven[x][1]
        #         evenFstAssists.append(resultEven[x][1])
        #         evenSndAssists.append()



        resultplayers=soup.find_all("font", attrs={"style":"cursor:hand;"} )

        tds=soup.find_all("td" )[1:]
        tds=[str(elem) for elem in tds]

        count=[]
        tds2=[]
    #     print tds

        for x in range(0,len(tds)):
            if "font style=" in tds[x]:
                count.append(tds[x].count ("font style="))
                tds2.append(tds[x])
    #     print tds2[2]
    #     print tds2
        if tds2!=[]:
            indices = [i for i, x in enumerate(tds2[2]) if x == ","]
        #     print tds2[2]
            temp=[]
            for x in range(0,len(indices)):
                if x==0:
                    temp.append(tds2[2][:indices[0]])
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x!=len(indices)-1:
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x==len(indices)-1:
                    temp.append(tds2[2][indices[x]:len(tds2[2])])
    #         print temp
            if temp!=[]:
                temp[0]=temp[0].replace("<td>", "")
        #     print temp

        #     print temp
            for x in range(0,len(temp)):
                temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                temp[x]=temp[x][0:(temp[x].index("<"))] 
            arrayTemp=[]

            indices = []

            arrayTemp=[]
            for y in range(1,len(tds2)):
                temp=[]
                indices = [i for i, x in enumerate(tds2[y]) if x == ","]
            #     print tds2[y]
            #     print indices
                for x in range(0,len(indices)):
                    if x==0:
                        temp.append(tds2[y][:indices[0]])
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x!=len(indices)-1:
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x==len(indices)-1:
                        temp.append(tds2[y][indices[x]:len(tds2[y])])
        #         print y
        #         print temp
                if temp!=[]:
                    temp[0]=temp[0].replace("<td>", "")
            #     print y
            #     print temp
                for x in range(0,len(temp)):
                    temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                    temp[x]=temp[x][0:(temp[x].index("<"))]
                arrayTemp.append(temp)



            resultTeam=[elem.find_all("td", attrs={"align":"left","class":"heading + bborder"} ) for elem in soup]
            homeTeam=resultTeam[0][3].text.strip()[:resultTeam[0][3].text.strip().index(" ")]
            awayTeam=resultTeam[0][4].text.strip()[:resultTeam[0][4].text.strip().index(" ")]
            resultTeam1= soup.find_all("tr", attrs={"class":"oddColor"} )
            resultTeam2=[elem.find_all("td", attrs={"align":"center"} ) for elem in resultTeam1]

            result1TeamEven= soup.find_all("tr", attrs={"class":"evenColor"} )
            result2TeamEven=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1TeamEven]
            oddGoalTeam=[]
            evenGoalTeam=[]
        #     print "EVENGoals"
        #     print ODDGoals
        #     print EVENGoals
        #     print arrayTemp
        #     print "evenarrayFailure"
        #     print evenarrayFailure
        #     # oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
        #     # print indicesloc

        #     print arrayTemp
    #         print 
            for x in range(0,ODDGoals):
                if x  not in oddarrayFailure:
                    oddGoalTeam.append(str(resultTeam2[x][4].text.strip()))
            print evenarrayFailure
            for x in range(0,EVENGoals):
        #         print x
                if x not in evenarrayFailure:
        #             print x
                    evenGoalTeam.append(str(result2TeamEven[x][4].text.strip()))

            indicesloc = [i for i, x in enumerate(arrayTemp) if x == []]
            # print arrayTemp.index([])
        #     print indicesloc 
            # indicesloc=[]
            indicesloc= [ elem/2  for elem in indicesloc if elem%2==0]
        #     print "result2TeamEven[indicesloc[0]]"
        #     print indicesloc
        #     print result2TeamEven[0]
        #     print result2TeamEven[1]
        #     print result2TeamEven[2]
        #     print result2TeamEven[3]
        #     print result2TeamEven[4]
        #     print result2TeamEven[5]
        #     print "result2TeamEven[indicesloc[0]/2]"
            # print result2TeamEven[indicesloc[0]/2]

            # print result2TeamEven
    #         print indicesloc
    #         print totalGoals
            # print result2TeamEven[indicesloc[0]]
    #         print evenGoalTeam
            for x in range(0,len(indicesloc)):
    #             print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0 and (indicesloc[x]!=totalGoals or indicesloc[x]!=totalGoals-1):
                    print "Even!"
                    oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals  and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1 and (indicesloc[x]!=totalGoals or indicesloc[x]!=totalGoals-1):
                    print "Odd!"
    #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
                    evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #         print indicesloc
    #         print totalGoals
    #         print evenGoalTeam
    #         [1]
    # 3
    # []
            oddArrayTemp=[]
            evenArrayTemp=[]
            for y in range(0,len(arrayTemp)):
                if y%4==1:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==0:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==2:
                    evenArrayTemp.append(arrayTemp[y]) 
                elif y%4==3:
                    evenArrayTemp.append(arrayTemp[y])
        #     print "oddArrayTemp"   
            # print arrayTemp.index([])

        #     print oddGoalTeam
        #     print evenGoalTeam
        #     print oddArrayTemp
        #     for y in range(0,len(oddArrayTemp)/2):
        #         if oddGoalTeam[y]==homeTeam:
        #             oddArrayTemp[2*y].append("W")
        #             oddArrayTemp[2*y+1].append("L")
        #         else:
        #             oddArrayTemp[2*y].append("L")
        #             oddArrayTemp[2*y+1].append("W")

        #     print evenArrayTemp
        #     print evenGoalTeam
        #     print evenarrayFailure
        #     print len(evenArrayTemp)
        #     print arrayTemp
        #     print len(evenArrayTemp)/2
        #     print len(evenGoalTeam)
        #     print evenGoalTeam
            evenArrayTemp=filter(lambda a: a != [], evenArrayTemp)
            oddArrayTemp=filter(lambda a: a != [], oddArrayTemp)
            # evenArrayTemp.remove([])
        #     print evenArrayTemp
    #         print oddGoalTeam
    #         print oddArrayTemp
    #         print evenGoalTeam
    #         print evenArrayTemp
            for y in range(0,len(oddArrayTemp)/2):
                if oddGoalTeam[y]==homeTeam:
                    oddArrayTemp[2*y].insert(0,"W")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"L")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    oddArrayTemp[2*y].insert(0,"L")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"W")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
    #         print evenArrayTemp
    #         print evenGoalTeam

            for y in range(0,len(evenArrayTemp)/2):
                if evenGoalTeam[y]==homeTeam:
                    evenArrayTemp[2*y].insert(0,"W")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"L")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    evenArrayTemp[2*y].insert(0,"L")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"W")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)

        #     for y in range(0,len(evenArrayTemp)/2):
        #     #     print y
        #         if evenGoalTeam[y]==homeTeam:
        #             evenArrayTemp[2*y].append("W")
        #             evenArrayTemp[2*y+1].append("L")
        #         else:
        #             evenArrayTemp[2*y].append("L")
        #             evenArrayTemp[2*y+1].append("W")

        #     print 
        #     print result2[1]
        #     print result2[2]
        #     print result2[3]
        #     print indicesloc
    #         print EVENGoals
    #         print result2[0]
    #         print result2[1]
    #         print result2[2]
    #         print result2[3]
    #         print totalGoals
    #         print indicesloc
#                 print "result2[0]"
#                 print result2[0]
#                 print result2[1]
#                 print result2[2]
    #         if len(resultEven[x])==3:
            for x in range(0,len(indicesloc)):
            #     print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0:
            #         evenGoalTeam.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
    #                 evenGoals.append(result2[EVENGoals][0])
    #                 evenFstAssists.append(result2[EVENGoals][1])
    #                 evenSndAssists.append(result2[EVENGoals][2])
                    if len(result2[ODDGoals])==3:
                        oddGoals.append(result2[ODDGoals][0])
                        oddFstAssists.append(result2[ODDGoals][1])
                        oddSndAssists.append(result2[ODDGoals][2])
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
            #         oddGoalTeam.append((str(resultTeam2[indicesloc[x]][4].text.strip())))
    #                 oddGoals.append(result2[ODDGoals][0])
    #                 oddFstAssists.append(result2[ODDGoals][1])
    #                 oddSndAssists.append(result2[ODDGoals][2])
#                     print "Yeah"
#                     print EVENGoals
#                     print result2TeamEven[0]
#                     print result2TeamEven[1]
#                     print result2TeamEven[2]
#                     print "resultEven[EVENGoals]"
#                     print resultEven[3]
#                     print resultEven[EVENGoals]
#                     print len(result2TeamEven[EVENGoals])
                    if len(resultEven[EVENGoals])==3:
#                         print "Yeah1"
                        evenGoals.append(resultEven[EVENGoals][0])
                        evenFstAssists.append(resultEven[EVENGoals][1])
                        evenSndAssists.append(resultEven[EVENGoals][2])

            # oddGoals.append(result2[ODDGoals][0])
            # oddFstAssists.append(result2[ODDGoals][1])
            # oddSndAssists.append(result2[ODDGoals][2])

            oddGoalsNumber= [str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddGoals]
            oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
            oddSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddSndAssists]
            evenGoalsNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenGoals]
            evenFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenFstAssists]
            evenSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenSndAssists ]
        #     print "evenGoalsNumber"
        #     print oddGoals
            # for x in range(0,len(indicesloc)):
            #     print x
            #     if indicesloc[x]%2==0:
            #         evenGoalsNumber.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
            #     else:
            #         oddGoalsNumber.append((str(resultTeam2[indicesloc[x]][4].text.strip())))

            goalOdd = []
            fstAssistOdd = []
            sndAssistOdd = []

            for y in range(0,len(oddGoalTeam)):
                goalOdd.append([])
                fstAssistOdd.append([])
                sndAssistOdd.append([])
#             print oddGoalsNumber
        #     print oddFstNumber
        #     print oddSndNumber
#             print oddGoalTeam

            for y in range(0,len(oddGoalTeam)):
                goalOdd[y].append(oddGoalsNumber[y])
                fstAssistOdd[y].append(oddFstNumber[y])
                sndAssistOdd[y].append(oddSndNumber[y])

            goalEven = []
            fstAssistEven = []
            sndAssistEven = []

            for y in range(0,len(evenGoalTeam)):
                goalEven.append([])
                fstAssistEven.append([])
                sndAssistEven.append([])

#             print evenGoalsNumber
#             print evenGoals
        #     print evenFstNumber
        #     print evenSndNumber
#             print evenGoalTeam
        #     print evenarrayFailure

            for y in range(0,len(evenGoalTeam)):
                goalEven[y].append(evenGoalsNumber[y])
                fstAssistEven[y].append(evenFstNumber[y])
                sndAssistEven[y].append(evenSndNumber[y])


            for y in range(0,len(goalEven)):
                if evenGoalTeam[y]==homeTeam:
                    goalEven[y].insert(0,str(homeTeam))
                    fstAssistEven[y].insert(0,str(homeTeam))
                    sndAssistEven[y].insert(0,str(homeTeam))
                else:
                    goalEven[y].insert(0,str(awayTeam))
                    fstAssistEven[y].insert(0,str(awayTeam))
                    sndAssistEven[y].insert(0,str(awayTeam))

        #     print "goalEven"
        #     print goalEven
        #     print fstAssistEven
        #     print sndAssistEven
    #         print oddGoalTeam
    #         print goalOdd
            for y in range(0,len(goalOdd)):
                if oddGoalTeam[y]==homeTeam:
                    goalOdd[y].insert(0,str(homeTeam))
                    fstAssistOdd[y].insert(0,str(homeTeam))
                    sndAssistOdd[y].insert(0,str(homeTeam))
                else:
                    goalOdd[y].insert(0,str(awayTeam))
                    fstAssistOdd[y].insert(0,str(awayTeam))
                    sndAssistOdd[y].insert(0,str(awayTeam))

        #     print "goalOdd"
        #     print goalOdd
        #     print fstAssistOdd
        #     print sndAssistOdd



        #     print goalEven+goalOdd
        #     print fstAssistEven+fstAssistOdd
        #     print sndAssistEven+sndAssistOdd
            Scorers.append(goalEven+goalOdd)
            FstAssistsPlayers.append(fstAssistEven+fstAssistOdd)
            SndAssistsPlayers.append(sndAssistEven+sndAssistOdd)
            plusMinusPlayers.append(evenArrayTemp+oddArrayTemp)
    elif numGames in [20036,20078,20232,20235,20290,20441,20461,20547,20755,20812,20846,20903,21025,21114,21144,21151,21164,21176]:   
        print numGames
        soup = BeautifulSoup(get_poll_xml1(numGames))
        # soup

        result1= soup.find_all("tr", attrs={"class":"oddColor"} )

        result2=[elem.find_all("td", attrs={"align":"left"} ) for elem in result1]

        resultEven= soup.find_all("tr", attrs={"class":"evenColor"} )

        resultEven=[elem.find_all("td", attrs={"align":"left"} ) for elem in resultEven]

        result3= soup.find_all("td", attrs={"align":"center", "style":"font-size: 40px;font-weight:bold"} )

        totalGoals=sum([int(elem.text.strip()) for elem in result3])

        if totalGoals%2==0:
            ODDGoals=totalGoals/2
            EVENGoals=totalGoals/2
        else:
            ODDGoals=totalGoals/2+1
            EVENGoals=totalGoals/2

        oddGoals=[]
        oddFstAssists=[]
        oddSndAssists=[]
        oddarrayFailure=[]
        for x in range(0,ODDGoals):
            if len(result2[x])==3:
                oddGoals.append(result2[x][0])
                oddFstAssists.append(result2[x][1])
                oddSndAssists.append(result2[x][2])
            else:
                oddarrayFailure.append(x)

        evenGoals=[]
        evenFstAssists=[]
        evenSndAssists=[]    
        evenarrayFailure=[]
        for x in range(0,EVENGoals):
        #     print "Test"
        #     print 
            if len(resultEven[x])==3:
                evenGoals.append(resultEven[x][0])
        #         print resultEven[x][1]
                evenFstAssists.append(resultEven[x][1])
                evenSndAssists.append(resultEven[x][2])
            else:
                evenarrayFailure.append(x)
        #     else:
        #         evenGoals.append(resultEven[x][0])
        # #         print resultEven[x][1]
        #         evenFstAssists.append(resultEven[x][1])
        #         evenSndAssists.append()



        resultplayers=soup.find_all("font", attrs={"style":"cursor:hand;"} )

        tds=soup.find_all("td" )[1:]
        tds=[str(elem) for elem in tds]

        count=[]
        tds2=[]
    #     print tds

        for x in range(0,len(tds)):
            if "font style=" in tds[x]:
                count.append(tds[x].count ("font style="))
                tds2.append(tds[x])
    #     print tds2[2]
    #     print tds2
        if tds2!=[]:
            indices = [i for i, x in enumerate(tds2[2]) if x == ","]
        #     print tds2[2]
            temp=[]
            for x in range(0,len(indices)):
                if x==0:
                    temp.append(tds2[2][:indices[0]])
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x!=len(indices)-1:
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x==len(indices)-1:
                    temp.append(tds2[2][indices[x]:len(tds2[2])])
    #         print temp
            if temp!=[]:
                temp[0]=temp[0].replace("<td>", "")
        #     print temp

        #     print temp
            for x in range(0,len(temp)):
                temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                temp[x]=temp[x][0:(temp[x].index("<"))] 
            arrayTemp=[]

            indices = []

            arrayTemp=[]
            for y in range(1,len(tds2)):
                temp=[]
                indices = [i for i, x in enumerate(tds2[y]) if x == ","]
            #     print tds2[y]
            #     print indices
                for x in range(0,len(indices)):
                    if x==0:
                        temp.append(tds2[y][:indices[0]])
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x!=len(indices)-1:
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x==len(indices)-1:
                        temp.append(tds2[y][indices[x]:len(tds2[y])])
        #         print y
        #         print temp
                if temp!=[]:
                    temp[0]=temp[0].replace("<td>", "")
            #     print y
            #     print temp
                for x in range(0,len(temp)):
                    temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                    temp[x]=temp[x][0:(temp[x].index("<"))]
                arrayTemp.append(temp)



            resultTeam=[elem.find_all("td", attrs={"align":"left","class":"heading + bborder"} ) for elem in soup]
            homeTeam=resultTeam[0][3].text.strip()[:resultTeam[0][3].text.strip().index(" ")]
            awayTeam=resultTeam[0][4].text.strip()[:resultTeam[0][4].text.strip().index(" ")]
            resultTeam1= soup.find_all("tr", attrs={"class":"oddColor"} )
            resultTeam2=[elem.find_all("td", attrs={"align":"center"} ) for elem in resultTeam1]

            result1TeamEven= soup.find_all("tr", attrs={"class":"evenColor"} )
            result2TeamEven=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1TeamEven]
            oddGoalTeam=[]
            evenGoalTeam=[]
        #     print "EVENGoals"
        #     print ODDGoals
        #     print EVENGoals
        #     print arrayTemp
        #     print "evenarrayFailure"
        #     print evenarrayFailure
        #     # oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
        #     # print indicesloc

        #     print arrayTemp
    #         print 
            for x in range(0,ODDGoals):
                if x  not in oddarrayFailure:
                    oddGoalTeam.append(str(resultTeam2[x][4].text.strip()))
#             print evenarrayFailure
            for x in range(0,EVENGoals):
        #         print x
                if x not in evenarrayFailure:
        #             print x
                    evenGoalTeam.append(str(result2TeamEven[x][4].text.strip()))

            indicesloc = [i for i, x in enumerate(arrayTemp) if x == []]
            # print arrayTemp.index([])
        #     print indicesloc 
            # indicesloc=[]
            indicesloc= [ elem/2  for elem in indicesloc if elem%2==0]
        #     print "result2TeamEven[indicesloc[0]]"
        #     print indicesloc
        #     print result2TeamEven[0]
        #     print result2TeamEven[1]
        #     print result2TeamEven[2]
        #     print result2TeamEven[3]
        #     print result2TeamEven[4]
        #     print result2TeamEven[5]
        #     print "result2TeamEven[indicesloc[0]/2]"
            # print result2TeamEven[indicesloc[0]/2]

            # print result2TeamEven
    #         print indicesloc
    #         print totalGoals
            # print result2TeamEven[indicesloc[0]]
    #         print evenGoalTeam
    #         for x in range(0,len(indicesloc)):
    # #             print x
    # #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
    #             if totalGoals%2==0:
    #                 print "Even!"
    #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    # #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    # #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals  and indicesloc[x]!=totalGoals-1):
    #             elif totalGoals%2==1:
    #                 print "Odd!"
    # #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    # #         print indicesloc
    # #         print totalGoals
    # #         print evenGoalTeam
    #         [1]
    # 3
    # []
            oddArrayTemp=[]
            evenArrayTemp=[]
            for y in range(0,len(arrayTemp)):
                if y%4==1:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==0:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==2:
                    evenArrayTemp.append(arrayTemp[y]) 
                elif y%4==3:
                    evenArrayTemp.append(arrayTemp[y])
        #     print "oddArrayTemp"   
            # print arrayTemp.index([])

        #     print oddGoalTeam
        #     print evenGoalTeam
        #     print oddArrayTemp
        #     for y in range(0,len(oddArrayTemp)/2):
        #         if oddGoalTeam[y]==homeTeam:
        #             oddArrayTemp[2*y].append("W")
        #             oddArrayTemp[2*y+1].append("L")
        #         else:
        #             oddArrayTemp[2*y].append("L")
        #             oddArrayTemp[2*y+1].append("W")

        #     print evenArrayTemp
        #     print evenGoalTeam
        #     print evenarrayFailure
        #     print len(evenArrayTemp)
        #     print arrayTemp
        #     print len(evenArrayTemp)/2
        #     print len(evenGoalTeam)
        #     print evenGoalTeam
            evenArrayTemp=filter(lambda a: a != [], evenArrayTemp)
            oddArrayTemp=filter(lambda a: a != [], oddArrayTemp)
            # evenArrayTemp.remove([])
        #     print evenArrayTemp
    #         print oddGoalTeam
    #         print oddArrayTemp
    #         print evenGoalTeam
    #         print evenArrayTemp
            for y in range(0,len(oddArrayTemp)/2):
                if oddGoalTeam[y]==homeTeam:
                    oddArrayTemp[2*y].insert(0,"W")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"L")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    oddArrayTemp[2*y].insert(0,"L")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"W")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
    #         print evenArrayTemp
    #         print evenGoalTeam

            for y in range(0,len(evenArrayTemp)/2):
                if evenGoalTeam[y]==homeTeam:
                    evenArrayTemp[2*y].insert(0,"W")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"L")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    evenArrayTemp[2*y].insert(0,"L")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"W")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)

        #     for y in range(0,len(evenArrayTemp)/2):
        #     #     print y
        #         if evenGoalTeam[y]==homeTeam:
        #             evenArrayTemp[2*y].append("W")
        #             evenArrayTemp[2*y+1].append("L")
        #         else:
        #             evenArrayTemp[2*y].append("L")
        #             evenArrayTemp[2*y+1].append("W")

        #     print 
        #     print result2[1]
        #     print result2[2]
        #     print result2[3]
        #     print indicesloc
    #         print EVENGoals
    #         print result2[0]
    #         print result2[1]
    #         print result2[2]
    #         print result2[3]
    #         print totalGoals
    #         print indicesloc
            print result2[EVENGoals]
    #         if len(resultEven[x])==3:
            for x in range(0,len(indicesloc)):
            #     print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0:
            #         evenGoalTeam.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
    #                 evenGoals.append(result2[EVENGoals][0])
    #                 evenFstAssists.append(result2[EVENGoals][1])
    #                 evenSndAssists.append(result2[EVENGoals][2])
                    if len(result2[ODDGoals])==3:
                        oddGoals.append(result2[ODDGoals][0])
                        oddFstAssists.append(result2[ODDGoals][1])
                        oddSndAssists.append(result2[ODDGoals][2])
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
            #         oddGoalTeam.append((str(resultTeam2[indicesloc[x]][4].text.strip())))
    #                 oddGoals.append(result2[ODDGoals][0])
    #                 oddFstAssists.append(result2[ODDGoals][1])
    #                 oddSndAssists.append(result2[ODDGoals][2])
#                     print "Yeah"
#                     print EVENGoals
#                     print result2TeamEven[0]
#                     print result2TeamEven[1]
#                     print result2TeamEven[2]
#                     print " result2TeamEven[3]"
#                     print result2TeamEven[3]
#                     print result2[ODDGoals]
#                     print len(result2TeamEven[EVENGoals])
                    if len(resultEven[EVENGoals])==3:
#                         print "Yeah1"
                        evenGoals.append(resultEven[EVENGoals][0])
                        evenFstAssists.append(resultEven[EVENGoals][1])
                        evenSndAssists.append(resultEven[EVENGoals][2])

            # oddGoals.append(result2[ODDGoals][0])
            # oddFstAssists.append(result2[ODDGoals][1])
            # oddSndAssists.append(result2[ODDGoals][2])

            oddGoalsNumber= [str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddGoals]
            oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
            oddSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddSndAssists]
            evenGoalsNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenGoals]
            evenFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenFstAssists]
            evenSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenSndAssists ]
        #     print "evenGoalsNumber"
        #     print oddGoals
            # for x in range(0,len(indicesloc)):
            #     print x
            #     if indicesloc[x]%2==0:
            #         evenGoalsNumber.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
            #     else:
            #         oddGoalsNumber.append((str(resultTeam2[indicesloc[x]][4].text.strip())))

            goalOdd = []
            fstAssistOdd = []
            sndAssistOdd = []

            for y in range(0,len(oddGoalTeam)):
                goalOdd.append([])
                fstAssistOdd.append([])
                sndAssistOdd.append([])
#             print oddGoalsNumber
        #     print oddFstNumber
        #     print oddSndNumber
#             print oddGoalTeam

            for y in range(0,len(oddGoalTeam)):
                goalOdd[y].append(oddGoalsNumber[y])
                fstAssistOdd[y].append(oddFstNumber[y])
                sndAssistOdd[y].append(oddSndNumber[y])

            goalEven = []
            fstAssistEven = []
            sndAssistEven = []

            for y in range(0,len(evenGoalTeam)):
                goalEven.append([])
                fstAssistEven.append([])
                sndAssistEven.append([])

#             print evenGoalsNumber
#             print evenGoals
        #     print evenFstNumber
        #     print evenSndNumber
#             print evenGoalTeam
        #     print evenarrayFailure

            for y in range(0,len(evenGoalTeam)):
                goalEven[y].append(evenGoalsNumber[y])
                fstAssistEven[y].append(evenFstNumber[y])
                sndAssistEven[y].append(evenSndNumber[y])


            for y in range(0,len(goalEven)):
                if evenGoalTeam[y]==homeTeam:
                    goalEven[y].insert(0,str(homeTeam))
                    fstAssistEven[y].insert(0,str(homeTeam))
                    sndAssistEven[y].insert(0,str(homeTeam))
                else:
                    goalEven[y].insert(0,str(awayTeam))
                    fstAssistEven[y].insert(0,str(awayTeam))
                    sndAssistEven[y].insert(0,str(awayTeam))

        #     print "goalEven"
        #     print goalEven
        #     print fstAssistEven
        #     print sndAssistEven
    #         print oddGoalTeam
    #         print goalOdd
            for y in range(0,len(goalOdd)):
                if oddGoalTeam[y]==homeTeam:
                    goalOdd[y].insert(0,str(homeTeam))
                    fstAssistOdd[y].insert(0,str(homeTeam))
                    sndAssistOdd[y].insert(0,str(homeTeam))
                else:
                    goalOdd[y].insert(0,str(awayTeam))
                    fstAssistOdd[y].insert(0,str(awayTeam))
                    sndAssistOdd[y].insert(0,str(awayTeam))

#             print "evenOdd"
#             print goalEven
        #     print fstAssistOdd
        #     print sndAssistOddresultEven



        #     print goalEven+goalOdd
        #     print fstAssistEven+fstAssistOdd
        #     print sndAssistEven+sndAssistOdd

            Scorers.append(goalEven+goalOdd)
            FstAssistsPlayers.append(fstAssistEven+fstAssistOdd)
            SndAssistsPlayers.append(sndAssistEven+sndAssistOdd)
            plusMinusPlayers.append(evenArrayTemp+oddArrayTemp)
print Scorers
newScorers=[]
for x in range(0,len(Scorers)):
    newScorers=newScorers+Scorers[x]
print newScorers
newFstAssistsPlayers=[]
for x in range(0,len(FstAssistsPlayers)):
    newFstAssistsPlayers=newFstAssistsPlayers+FstAssistsPlayers[x]
print newFstAssistsPlayers
newSndAssistsPlayers=[]
for x in range(0,len(SndAssistsPlayers)):
    newSndAssistsPlayers=newSndAssistsPlayers+SndAssistsPlayers[x]
print newSndAssistsPlayers
print len(newScorers)
print len(newFstAssistsPlayers)
print len(newSndAssistsPlayers)
print FstAssistsPlayers
print SndAssistsPlayers
print len(Scorers)
print len(FstAssistsPlayers)
print len(SndAssistsPlayers)
print plusMinusPlayers
print len(plusMinusPlayers)
print np.unique(newScorers)
# print list(set(zip(*newScorers)[1]))
uniqueNewScorers=[]
for x in range(0,len(newScorers)):
    if newScorers[x] not in uniqueNewScorers:
        uniqueNewScorers.append(newScorers[x])
print uniqueNewScorers
print len(uniqueNewScorers)
sortedUniqueNewScorers= sorted(uniqueNewScorers)
uniqueNewFstAssistsPlayers=[]

for x in range(0,len(newFstAssistsPlayers)):
    if newFstAssistsPlayers[x] not in uniqueNewFstAssistsPlayers:
        uniqueNewFstAssistsPlayers.append(newFstAssistsPlayers[x])

sortedUniqueNewFstAssistsPlayers= sorted(uniqueNewFstAssistsPlayers)

uniqueNewSndAssistsPlayers=[]
for x in range(0,len(newSndAssistsPlayers)):
    if newSndAssistsPlayers[x] not in uniqueNewSndAssistsPlayers:
        uniqueNewSndAssistsPlayers.append(newSndAssistsPlayers[x])

sortedUniqueNewSndAssistsPlayers= sorted(uniqueNewSndAssistsPlayers)

for x in range(0,len(sortedUniqueNewScorers)):
    counter=0
    for y in range(0,len(newScorers)):
        if sortedUniqueNewScorers[x]==newScorers[y]:
            counter=counter+1
    sortedUniqueNewScorers[x].append(counter)
print sortedUniqueNewScorers

for x in range(0,len(sortedUniqueNewFstAssistsPlayers)):
    counter=0
    for y in range(0,len(newFstAssistsPlayers)):
        if sortedUniqueNewFstAssistsPlayers[x]==newFstAssistsPlayers[y]:
            counter=counter+1
    sortedUniqueNewFstAssistsPlayers[x].append(counter)
print sortedUniqueNewFstAssistsPlayers

for x in range(0,len(sortedUniqueNewSndAssistsPlayers)):
    counter=0
    for y in range(0,len(newSndAssistsPlayers)):
        if sortedUniqueNewSndAssistsPlayers[x]==newSndAssistsPlayers[y]:
            counter=counter+1
    sortedUniqueNewSndAssistsPlayers[x].append(counter)
print sortedUniqueNewSndAssistsPlayers


20001
20002
20003
20004
20005
20006
20007
Even!
20008
20009
20010
20011
20012
20013
20014
20015
20016
20017
20018
20019
20020
20021
20022
20023
20024
20025
20026
20027
20028
20029
20030
20031
20032
20033
20034
20035
20036
[<td align="left">
<table border="0" cellpadding="0" cellspacing="0">
<tr>
<td align="right" width="15">19</td>
<td> </td>
<td> </td>
<td>P.MAROON</td>
</tr>
</table>
</td>, <td align="left">Tripping</td>]
20037
20038
20039
20040
20041
20042
20043
20044
20045
20046
20047
20048
20049
20050
20051
20052
20053
20054
20055
20056
20057
20058
20059
20060
20061
20062
20063
20064
20065
Odd!
20066
20067
Even!
20068
20069
20070
20071
20072
20073
20074
20075
20076
20077
20078
[<td align="left">93 R.NUGENT-HOPKINS(1)</td>, <td align="left">14 J.EBERLE(3)</td>, <td align="left">
</td>]
20079
20080
20081
20082
20083
20084
20085
20086
20087
20088
20089
20090
20091
20092
20093
20094
20095
20096
20097
20098
20099
20100
20101
20102
20103
20104
20105
20106
20107
20108
20109
20110
20111
2

In [1]:

import json
import unicodedata
import numpy as np
import networkx as nx
import requests
from pattern import web
import matplotlib.pyplot as plt

# set some nicer defaults for matplotlib
from matplotlib import rcParams

def get_poll_xml1(poll_id):
    url = "http://www.nhl.com/scores/htmlreports/20142015/GS0%i.HTM" % int(poll_id)
    return requests.get(url
                       ).text

from bs4 import BeautifulSoup
Scorers=[]
FstAssistsPlayers=[]
SndAssistsPlayers=[]
plusMinusPlayers=[]
# [20036,20461,20846,21114,21151,21164,21176]:
# [20036,20149,20235,20332,20461,20742,20846,21114,21151,21164,21176]:
for numGames in range(20001,21231):
    if numGames not in [20036,20078,20149,20232,20235,20290,20332,20441,20461,20547,20742,20755,20812,20846,20903,21025,21114,21144,21151,21164,21176]:
        print numGames
        soup = BeautifulSoup(get_poll_xml1(numGames))
        # soup

        result1= soup.find_all("tr", attrs={"class":"oddColor"} )
#         resultCenter= soup.find_all("td", attrs={"align":"center","class":"oddColor"} )
#         resultCen= result1.find_all("td", attrs={"align":"center"} )
        resultCen=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1]
#         print resultCen
        
        result2=[elem.find_all("td", attrs={"align":"left"} ) for elem in result1]

        resultEven= soup.find_all("tr", attrs={"class":"evenColor"} )

        resultEven=[elem.find_all("td", attrs={"align":"left"} ) for elem in resultEven]

        result3= soup.find_all("td", attrs={"align":"center", "style":"font-size: 40px;font-weight:bold"} )

        totalGoals=sum([int(elem.text.strip()) for elem in result3])

        if totalGoals%2==0:
            ODDGoals=totalGoals/2
            EVENGoals=totalGoals/2
        else:
            ODDGoals=totalGoals/2+1
            EVENGoals=totalGoals/2

        oddGoals=[]
        oddFstAssists=[]
        oddSndAssists=[]
        oddarrayFailure=[]
        for x in range(0,ODDGoals):
            if len(result2[x])==3:
                oddGoals.append(result2[x][0])
                oddFstAssists.append(result2[x][1])
                oddSndAssists.append(result2[x][2])
            else:
                oddarrayFailure.append(x)

        evenGoals=[]
        evenFstAssists=[]
        evenSndAssists=[]    
        evenarrayFailure=[]
        for x in range(0,EVENGoals):
        #     print "Test"
        #     print 
            if len(resultEven[x])==3:
                evenGoals.append(resultEven[x][0])
        #         print resultEven[x][1]
                evenFstAssists.append(resultEven[x][1])
                evenSndAssists.append(resultEven[x][2])
            else:
                evenarrayFailure.append(x)
        #     else:
        #         evenGoals.append(resultEven[x][0])
        # #         print resultEven[x][1]
        #         evenFstAssists.append(resultEven[x][1])
        #         evenSndAssists.append()



        resultplayers=soup.find_all("font", attrs={"style":"cursor:hand;"} )

        tds=soup.find_all("td" )[1:]
        tds=[str(elem) for elem in tds]

        count=[]
        tds2=[]
    #     print tds

        for x in range(0,len(tds)):
            if "font style=" in tds[x]:
                count.append(tds[x].count ("font style="))
                tds2.append(tds[x])
    #     print tds2[2]
    #     print tds2
        if tds2!=[]:
            indices = [i for i, x in enumerate(tds2[2]) if x == ","]
        #     print tds2[2]
            temp=[]
            for x in range(0,len(indices)):
                if x==0:
                    temp.append(tds2[2][:indices[0]])
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x!=len(indices)-1:
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x==len(indices)-1:
                    temp.append(tds2[2][indices[x]:len(tds2[2])])
    #         print temp
            if temp!=[]:
                temp[0]=temp[0].replace("<td>", "")
        #     print temp

        #     print temp
            for x in range(0,len(temp)):
                temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                temp[x]=temp[x][0:(temp[x].index("<"))] 
            arrayTemp=[]

            indices = []

            arrayTemp=[]
            for y in range(1,len(tds2)):
                temp=[]
                indices = [i for i, x in enumerate(tds2[y]) if x == ","]
            #     print tds2[y]
            #     print indices
                for x in range(0,len(indices)):
                    if x==0:
                        temp.append(tds2[y][:indices[0]])
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x!=len(indices)-1:
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x==len(indices)-1:
                        temp.append(tds2[y][indices[x]:len(tds2[y])])
        #         print y
        #         print temp
                if temp!=[]:
                    temp[0]=temp[0].replace("<td>", "")
            #     print y
            #     print temp
                for x in range(0,len(temp)):
                    temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                    temp[x]=temp[x][0:(temp[x].index("<"))]
                arrayTemp.append(temp)



            resultTeam=[elem.find_all("td", attrs={"align":"left","class":"heading + bborder"} ) for elem in soup]
            homeTeam=resultTeam[0][3].text.strip()[:resultTeam[0][3].text.strip().index(" ")]
            awayTeam=resultTeam[0][4].text.strip()[:resultTeam[0][4].text.strip().index(" ")]
            resultTeam1= soup.find_all("tr", attrs={"class":"oddColor"} )
            resultTeam2=[elem.find_all("td", attrs={"align":"center"} ) for elem in resultTeam1]

            result1TeamEven= soup.find_all("tr", attrs={"class":"evenColor"} )
            result2TeamEven=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1TeamEven]
            oddGoalTeam=[]
            evenGoalTeam=[]
        #     print "EVENGoals"
        #     print ODDGoals
        #     print EVENGoals
        #     print arrayTemp
#             print "evenarrayFailure"
#             print evenarrayFailure
        #     # oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
        #     # print indicesloc

        #     print arrayTemp
    #         print 
            for x in range(0,ODDGoals):
                if x  not in oddarrayFailure:
                    oddGoalTeam.append(str(resultTeam2[x][4].text.strip()))
#             print evenarrayFailure
            for x in range(0,EVENGoals):
        #         print x
                if x not in evenarrayFailure:
        #             print x
                    evenGoalTeam.append(str(result2TeamEven[x][4].text.strip()))

            indicesloc = [i for i, x in enumerate(arrayTemp) if x == []]
            # print arrayTemp.index([])
        #     print indicesloc 
            # indicesloc=[]
            indicesloc= [ elem/2  for elem in indicesloc if elem%2==0]
        #     print "result2TeamEven[indicesloc[0]]"
        #     print indicesloc
        #     print result2TeamEven[0]
        #     print result2TeamEven[1]
        #     print result2TeamEven[2]
        #     print result2TeamEven[3]
        #     print result2TeamEven[4]
        #     print result2TeamEven[5]
        #     print "result2TeamEven[indicesloc[0]/2]"
            # print result2TeamEven[indicesloc[0]/2]

            # print result2TeamEven
    #         print indicesloc
    #         print totalGoals
            # print result2TeamEven[indicesloc[0]]
    #         print evenGoalTeam
#             print "result2[0]"
#             print result2[0]
#             print result2[1]
#             print result2[2]
            
            totalGoals1=totalGoals
            for x in range(0,len(indicesloc)):
    #             print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                totalGoals1=totalGoals1+1
                if totalGoals%2==0:
                    print "Even!"
                    oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals  and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
                    print "Odd!"
    #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
                    evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #         print indicesloc
    #         print totalGoals
    #         print evenGoalTeam
            if totalGoals%2==0:
                ODDGoals1=totalGoals1/2
                EVENGoals1=totalGoals1/2
            else:
                ODDGoals1=totalGoals1/2+1
                EVENGoals1=totalGoals1/2
#             print "resultCen[totalGoals1]"
#             print resultCen[EVENGoals1][2]
#             print resultCen[ODDGoals1][2]
#             print resultCen[EVENGoals1][1]
#             print resultCen[ODDGoals1][1]
#             print resultCen[EVENGoals1][0]
            resultCenEVENGoals1=str(resultCen[EVENGoals1][1])
#             print resultCenEVENGoals1[(resultCenEVENGoals1.index(">")+1):len(resultCenEVENGoals1)]
#             print str(resultCen[EVENGoals1][1])
#             print str(resultCen[EVENGoals1][1])[(str(resultCen[EVENGoals1][1]).index(">")+1):]
            if totalGoals1%2==1:
                strtemp=str(resultCen[EVENGoals1][1])[(str(resultCen[EVENGoals1][1]).index(">"))+1:]
                strtemp=strtemp[0:(strtemp.index("<"))] 
                manPower=str(resultCen[EVENGoals1][3])[(str(resultCen[EVENGoals1][3]).index(">"))+1:]
                manPower=manPower[0:(manPower.index("<"))] 
            else:
                strtemp=str(resultCen[ODDGoals1][1])[(str(resultCen[ODDGoals1][1]).index(">"))+1:]
                strtemp=strtemp[0:(strtemp.index("<"))]
                manPower=str(resultCen[ODDGoals1][3])[(str(resultCen[ODDGoals1][3]).index(">"))+1:]
                manPower=manPower[0:(manPower.index("<"))] 
#             print strtemp
            print resultCen[ODDGoals1][3]
            
#         <td align="center">SO</td>
#             temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
#                 temp[x]=temp[x][0:(temp[x].index("<"))] 

#             print resultCen[ODDGoals1][0]
            
                
    #         [1]
    # 3
    # []
            oddArrayTemp=[]
            evenArrayTemp=[]
            for y in range(0,len(arrayTemp)):
                if y%4==1:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==0:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==2:
                    evenArrayTemp.append(arrayTemp[y]) 
                elif y%4==3:
                    evenArrayTemp.append(arrayTemp[y])
        #     print "oddArrayTemp"   
            # print arrayTemp.index([])

        #     print oddGoalTeam
        #     print evenGoalTeam
        #     print oddArrayTemp
        #     for y in range(0,len(oddArrayTemp)/2):
        #         if oddGoalTeam[y]==homeTeam:
        #             oddArrayTemp[2*y].append("W")
        #             oddArrayTemp[2*y+1].append("L")
        #         else:
        #             oddArrayTemp[2*y].append("L")
        #             oddArrayTemp[2*y+1].append("W")

        #     print evenArrayTemp
        #     print evenGoalTeam
        #     print evenarrayFailure
        #     print len(evenArrayTemp)
        #     print arrayTemp
        #     print len(evenArrayTemp)/2
        #     print len(evenGoalTeam)
        #     print evenGoalTeam
            evenArrayTemp=filter(lambda a: a != [], evenArrayTemp)
            oddArrayTemp=filter(lambda a: a != [], oddArrayTemp)
            # evenArrayTemp.remove([])
        #     print evenArrayTemp
    #         print oddGoalTeam
    #         print oddArrayTemp
    #         print evenGoalTeam
    #         print evenArrayTemp
            for y in range(0,len(oddArrayTemp)/2):
                if oddGoalTeam[y]==homeTeam:
                    oddArrayTemp[2*y].insert(0,"W")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"L")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    oddArrayTemp[2*y].insert(0,"L")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"W")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
    #         print evenArrayTemp
    #         print evenGoalTeam

            for y in range(0,len(evenArrayTemp)/2):
                if evenGoalTeam[y]==homeTeam:
                    evenArrayTemp[2*y].insert(0,"W")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"L")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    evenArrayTemp[2*y].insert(0,"L")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"W")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)

        #     for y in range(0,len(evenArrayTemp)/2):
        #     #     print y
        #         if evenGoalTeam[y]==homeTeam:
        #             evenArrayTemp[2*y].append("W")
        #             evenArrayTemp[2*y+1].append("L")
        #         else:
        #             evenArrayTemp[2*y].append("L")
        #             evenArrayTemp[2*y+1].append("W")

        #     print 
        #     print result2[1]
        #     print result2[2]
        #     print result2[3]
        #     print indicesloc
    #         print totalGoals
    #         print indicesloc
            for x in range(0,len(indicesloc)):
            #     print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0:
            #         evenGoalTeam.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
    #                 evenGoals.append(result2[EVENGoals][0])
    #                 evenFstAssists.append(result2[EVENGoals][1])
    #                 evenSndAssists.append(result2[EVENGoals][2])
                    if len(result2[ODDGoals])==3:
                        oddGoals.append(result2[ODDGoals][0])
                        oddFstAssists.append(result2[ODDGoals][1])
                        oddSndAssists.append(result2[ODDGoals][2])
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
            #         oddGoalTeam.append((str(resultTeam2[indicesloc[x]][4].text.strip())))
    #                 oddGoals.append(result2[ODDGoals][0])
    #                 oddFstAssists.append(result2[ODDGoals][1])
    #                 oddSndAssists.append(result2[ODDGoals][2])
#                     print resultEven
                    if len(resultEven[EVENGoals])==3:
                        evenGoals.append(resultEven[EVENGoals][0])
                        evenFstAssists.append(resultEven[EVENGoals][1])
                        evenSndAssists.append(resultEven[EVENGoals][2])

            # oddGoals.append(result2[ODDGoals][0])
            # oddFstAssists.append(result2[ODDGoals][1])
            # oddSndAssists.append(result2[ODDGoals][2])

            oddGoalsNumber= [str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddGoals]
            oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
            oddSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddSndAssists]
            evenGoalsNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenGoals]
            evenFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenFstAssists]
            evenSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenSndAssists ]
        #     print "evenGoalsNumber"
        #     print oddGoals
            # for x in range(0,len(indicesloc)):
            #     print x
            #     if indicesloc[x]%2==0:
            #         evenGoalsNumber.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
            #     else:
            #         oddGoalsNumber.append((str(resultTeam2[indicesloc[x]][4].text.strip())))

            goalOdd = []
            fstAssistOdd = []
            sndAssistOdd = []

            for y in range(0,len(oddGoalTeam)):
                goalOdd.append([])
                fstAssistOdd.append([])
                sndAssistOdd.append([])
        #     print oddGoalsNumber
        #     print oddFstNumber
        #     print oddSndNumber
        #     print oddGoalTeam
            for y in range(0,len(oddGoalTeam)):
                goalOdd[y].append(oddGoalsNumber[y])
                fstAssistOdd[y].append(oddFstNumber[y])
                sndAssistOdd[y].append(oddSndNumber[y])

            goalEven = []
            fstAssistEven = []
            sndAssistEven = []

            for y in range(0,len(evenGoalTeam)):
                goalEven.append([])
                fstAssistEven.append([])
                sndAssistEven.append([])

#             print evenGoalsNumber
        #     print evenFstNumber
        #     print evenSndNumber
#             print evenGoalTeam
        #     print evenarrayFailure
        
            for y in range(0,len(evenGoalTeam)):
                goalEven[y].append(evenGoalsNumber[y])
                fstAssistEven[y].append(evenFstNumber[y])
                sndAssistEven[y].append(evenSndNumber[y])


            for y in range(0,len(goalEven)):
                if evenGoalTeam[y]==homeTeam:
                    goalEven[y].insert(0,str(homeTeam))
                    fstAssistEven[y].insert(0,str(homeTeam))
                    sndAssistEven[y].insert(0,str(homeTeam))
                else:
                    goalEven[y].insert(0,str(awayTeam))
                    fstAssistEven[y].insert(0,str(awayTeam))
                    sndAssistEven[y].insert(0,str(awayTeam))

        #     print "goalEven"
        #     print goalEven
        #     print fstAssistEven
        #     print sndAssistEven
    #         print oddGoalTeam
    #         print goalOdd
            for y in range(0,len(goalOdd)):
                if oddGoalTeam[y]==homeTeam:
                    goalOdd[y].insert(0,str(homeTeam))
                    fstAssistOdd[y].insert(0,str(homeTeam))
                    sndAssistOdd[y].insert(0,str(homeTeam))
                else:
                    goalOdd[y].insert(0,str(awayTeam))
                    fstAssistOdd[y].insert(0,str(awayTeam))
                    sndAssistOdd[y].insert(0,str(awayTeam))

        #     print "goalOdd"
        #     print goalOdd
        #     print fstAssistOdd
        #     print sndAssistOdd



        #     print goalEven+goalOdd
        #     print fstAssistEven+fstAssistOdd
        #     print sndAssistEven+sndAssistOdd
#             print "evenArrayTemp+oddArrayTemp"
#             print evenArrayTemp+oddArrayTemp
            Goal=goalEven+goalOdd
            FstAssist=fstAssistEven+fstAssistOdd
            SndAssist=sndAssistEven+sndAssistOdd
            ArrayTemp=evenArrayTemp+oddArrayTemp
            print "strtemp"
            print strtemp
            print manPower
            if manPower=="SH-EN":
                del ArrayTemp[-1]
                del FstAssist[-1]
                del SndAssist[-1]
                del Goal[-1]
            if strtemp=="SO":
                del ArrayTemp[-1]
                del FstAssist[-1]
                del SndAssist[-1]
                del Goal[-1]
            
            Scorers.append(Goal)
            FstAssistsPlayers.append(FstAssist)
            SndAssistsPlayers.append(SndAssist)
            plusMinusPlayers.append(ArrayTemp)
#     elif numGames in [20149,20235,20332,20742]:
    elif numGames in [20149,20332,20742]:
        # [20036,20149,20235,20332,20461,20742,20846,21114,21151,21164,21176]:
#             [20149,20235,20332,20742]:
        print numGames
        soup = BeautifulSoup(get_poll_xml1(numGames))
        # soup

        result1= soup.find_all("tr", attrs={"class":"oddColor"} )

        result2=[elem.find_all("td", attrs={"align":"left"} ) for elem in result1]

        resultEven= soup.find_all("tr", attrs={"class":"evenColor"} )

        resultEven=[elem.find_all("td", attrs={"align":"left"} ) for elem in resultEven]

        result3= soup.find_all("td", attrs={"align":"center", "style":"font-size: 40px;font-weight:bold"} )

        totalGoals=sum([int(elem.text.strip()) for elem in result3])

        if totalGoals%2==0:
            ODDGoals=totalGoals/2
            EVENGoals=totalGoals/2
        else:
            ODDGoals=totalGoals/2+1
            EVENGoals=totalGoals/2

        oddGoals=[]
        oddFstAssists=[]
        oddSndAssists=[]
        oddarrayFailure=[]
        for x in range(0,ODDGoals):
            if len(result2[x])==3:
                oddGoals.append(result2[x][0])
                oddFstAssists.append(result2[x][1])
                oddSndAssists.append(result2[x][2])
            else:
                oddarrayFailure.append(x)

        evenGoals=[]
        evenFstAssists=[]
        evenSndAssists=[]    
        evenarrayFailure=[]
        for x in range(0,EVENGoals):
        #     print "Test"
        #     print 
            if len(resultEven[x])==3:
                evenGoals.append(resultEven[x][0])
        #         print resultEven[x][1]
                evenFstAssists.append(resultEven[x][1])
                evenSndAssists.append(resultEven[x][2])
            else:
                evenarrayFailure.append(x)
        #     else:
        #         evenGoals.append(resultEven[x][0])
        # #         print resultEven[x][1]
        #         evenFstAssists.append(resultEven[x][1])
        #         evenSndAssists.append()



        resultplayers=soup.find_all("font", attrs={"style":"cursor:hand;"} )

        tds=soup.find_all("td" )[1:]
        tds=[str(elem) for elem in tds]

        count=[]
        tds2=[]
    #     print tds

        for x in range(0,len(tds)):
            if "font style=" in tds[x]:
                count.append(tds[x].count ("font style="))
                tds2.append(tds[x])
    #     print tds2[2]
    #     print tds2
        if tds2!=[]:
            indices = [i for i, x in enumerate(tds2[2]) if x == ","]
        #     print tds2[2]
            temp=[]
            for x in range(0,len(indices)):
                if x==0:
                    temp.append(tds2[2][:indices[0]])
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x!=len(indices)-1:
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x==len(indices)-1:
                    temp.append(tds2[2][indices[x]:len(tds2[2])])
    #         print temp
            if temp!=[]:
                temp[0]=temp[0].replace("<td>", "")
        #     print temp

        #     print temp
            for x in range(0,len(temp)):
                temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                temp[x]=temp[x][0:(temp[x].index("<"))] 
            arrayTemp=[]

            indices = []

            arrayTemp=[]
            for y in range(1,len(tds2)):
                temp=[]
                indices = [i for i, x in enumerate(tds2[y]) if x == ","]
            #     print tds2[y]
            #     print indices
                for x in range(0,len(indices)):
                    if x==0:
                        temp.append(tds2[y][:indices[0]])
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x!=len(indices)-1:
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x==len(indices)-1:
                        temp.append(tds2[y][indices[x]:len(tds2[y])])
        #         print y
        #         print temp
                if temp!=[]:
                    temp[0]=temp[0].replace("<td>", "")
            #     print y
            #     print temp
                for x in range(0,len(temp)):
                    temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                    temp[x]=temp[x][0:(temp[x].index("<"))]
                arrayTemp.append(temp)



            resultTeam=[elem.find_all("td", attrs={"align":"left","class":"heading + bborder"} ) for elem in soup]
            homeTeam=resultTeam[0][3].text.strip()[:resultTeam[0][3].text.strip().index(" ")]
            awayTeam=resultTeam[0][4].text.strip()[:resultTeam[0][4].text.strip().index(" ")]
            resultTeam1= soup.find_all("tr", attrs={"class":"oddColor"} )
            resultTeam2=[elem.find_all("td", attrs={"align":"center"} ) for elem in resultTeam1]

            result1TeamEven= soup.find_all("tr", attrs={"class":"evenColor"} )
            result2TeamEven=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1TeamEven]
            oddGoalTeam=[]
            evenGoalTeam=[]
        #     print "EVENGoals"
        #     print ODDGoals
        #     print EVENGoals
        #     print arrayTemp
        #     print "evenarrayFailure"
        #     print evenarrayFailure
        #     # oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
        #     # print indicesloc

        #     print arrayTemp
    #         print 
            for x in range(0,ODDGoals):
                if x  not in oddarrayFailure:
                    oddGoalTeam.append(str(resultTeam2[x][4].text.strip()))
            print evenarrayFailure
            for x in range(0,EVENGoals):
        #         print x
                if x not in evenarrayFailure:
        #             print x
                    evenGoalTeam.append(str(result2TeamEven[x][4].text.strip()))

            indicesloc = [i for i, x in enumerate(arrayTemp) if x == []]
            # print arrayTemp.index([])
        #     print indicesloc 
            # indicesloc=[]
            indicesloc= [ elem/2  for elem in indicesloc if elem%2==0]
        #     print "result2TeamEven[indicesloc[0]]"
        #     print indicesloc
        #     print result2TeamEven[0]
        #     print result2TeamEven[1]
        #     print result2TeamEven[2]
        #     print result2TeamEven[3]
        #     print result2TeamEven[4]
        #     print result2TeamEven[5]
        #     print "result2TeamEven[indicesloc[0]/2]"
            # print result2TeamEven[indicesloc[0]/2]

            # print result2TeamEven
    #         print indicesloc
    #         print totalGoals
            # print result2TeamEven[indicesloc[0]]
    #         print evenGoalTeam
            for x in range(0,len(indicesloc)):
    #             print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0 and (indicesloc[x]!=totalGoals or indicesloc[x]!=totalGoals-1):
                    print "Even!"
                    oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals  and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1 and (indicesloc[x]!=totalGoals or indicesloc[x]!=totalGoals-1):
                    print "Odd!"
    #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
                    evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #         print indicesloc
    #         print totalGoals
    #         print evenGoalTeam
    #         [1]
    # 3
    # []
            oddArrayTemp=[]
            evenArrayTemp=[]
            for y in range(0,len(arrayTemp)):
                if y%4==1:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==0:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==2:
                    evenArrayTemp.append(arrayTemp[y]) 
                elif y%4==3:
                    evenArrayTemp.append(arrayTemp[y])
        #     print "oddArrayTemp"   
            # print arrayTemp.index([])

        #     print oddGoalTeam
        #     print evenGoalTeam
        #     print oddArrayTemp
        #     for y in range(0,len(oddArrayTemp)/2):
        #         if oddGoalTeam[y]==homeTeam:
        #             oddArrayTemp[2*y].append("W")
        #             oddArrayTemp[2*y+1].append("L")
        #         else:
        #             oddArrayTemp[2*y].append("L")
        #             oddArrayTemp[2*y+1].append("W")

        #     print evenArrayTemp
        #     print evenGoalTeam
        #     print evenarrayFailure
        #     print len(evenArrayTemp)
        #     print arrayTemp
        #     print len(evenArrayTemp)/2
        #     print len(evenGoalTeam)
        #     print evenGoalTeam
            evenArrayTemp=filter(lambda a: a != [], evenArrayTemp)
            oddArrayTemp=filter(lambda a: a != [], oddArrayTemp)
            # evenArrayTemp.remove([])
        #     print evenArrayTemp
    #         print oddGoalTeam
    #         print oddArrayTemp
    #         print evenGoalTeam
    #         print evenArrayTemp
            for y in range(0,len(oddArrayTemp)/2):
                if oddGoalTeam[y]==homeTeam:
                    oddArrayTemp[2*y].insert(0,"W")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"L")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    oddArrayTemp[2*y].insert(0,"L")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"W")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
    #         print evenArrayTemp
    #         print evenGoalTeam

            for y in range(0,len(evenArrayTemp)/2):
                if evenGoalTeam[y]==homeTeam:
                    evenArrayTemp[2*y].insert(0,"W")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"L")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    evenArrayTemp[2*y].insert(0,"L")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"W")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)

        #     for y in range(0,len(evenArrayTemp)/2):
        #     #     print y
        #         if evenGoalTeam[y]==homeTeam:
        #             evenArrayTemp[2*y].append("W")
        #             evenArrayTemp[2*y+1].append("L")
        #         else:
        #             evenArrayTemp[2*y].append("L")
        #             evenArrayTemp[2*y+1].append("W")

        #     print 
        #     print result2[1]
        #     print result2[2]
        #     print result2[3]
        #     print indicesloc
    #         print EVENGoals
    #         print result2[0]
    #         print result2[1]
    #         print result2[2]
    #         print result2[3]
    #         print totalGoals
    #         print indicesloc
#                 print "result2[0]"
#                 print result2[0]
#                 print result2[1]
#                 print result2[2]
    #         if len(resultEven[x])==3:
            for x in range(0,len(indicesloc)):
            #     print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0:
            #         evenGoalTeam.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
    #                 evenGoals.append(result2[EVENGoals][0])
    #                 evenFstAssists.append(result2[EVENGoals][1])
    #                 evenSndAssists.append(result2[EVENGoals][2])
                    if len(result2[ODDGoals])==3:
                        oddGoals.append(result2[ODDGoals][0])
                        oddFstAssists.append(result2[ODDGoals][1])
                        oddSndAssists.append(result2[ODDGoals][2])
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
            #         oddGoalTeam.append((str(resultTeam2[indicesloc[x]][4].text.strip())))
    #                 oddGoals.append(result2[ODDGoals][0])
    #                 oddFstAssists.append(result2[ODDGoals][1])
    #                 oddSndAssists.append(result2[ODDGoals][2])
#                     print "Yeah"
#                     print EVENGoals
#                     print result2TeamEven[0]
#                     print result2TeamEven[1]
#                     print result2TeamEven[2]
#                     print "resultEven[EVENGoals]"
#                     print resultEven[3]
#                     print resultEven[EVENGoals]
#                     print len(result2TeamEven[EVENGoals])
                    if len(resultEven[EVENGoals])==3:
#                         print "Yeah1"
                        evenGoals.append(resultEven[EVENGoals][0])
                        evenFstAssists.append(resultEven[EVENGoals][1])
                        evenSndAssists.append(resultEven[EVENGoals][2])

            # oddGoals.append(result2[ODDGoals][0])
            # oddFstAssists.append(result2[ODDGoals][1])
            # oddSndAssists.append(result2[ODDGoals][2])

            oddGoalsNumber= [str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddGoals]
            oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
            oddSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddSndAssists]
            evenGoalsNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenGoals]
            evenFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenFstAssists]
            evenSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenSndAssists ]
        #     print "evenGoalsNumber"
        #     print oddGoals
            # for x in range(0,len(indicesloc)):
            #     print x
            #     if indicesloc[x]%2==0:
            #         evenGoalsNumber.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
            #     else:
            #         oddGoalsNumber.append((str(resultTeam2[indicesloc[x]][4].text.strip())))

            goalOdd = []
            fstAssistOdd = []
            sndAssistOdd = []

            for y in range(0,len(oddGoalTeam)):
                goalOdd.append([])
                fstAssistOdd.append([])
                sndAssistOdd.append([])
#             print oddGoalsNumber
        #     print oddFstNumber
        #     print oddSndNumber
#             print oddGoalTeam

            for y in range(0,len(oddGoalTeam)):
                goalOdd[y].append(oddGoalsNumber[y])
                fstAssistOdd[y].append(oddFstNumber[y])
                sndAssistOdd[y].append(oddSndNumber[y])

            goalEven = []
            fstAssistEven = []
            sndAssistEven = []

            for y in range(0,len(evenGoalTeam)):
                goalEven.append([])
                fstAssistEven.append([])
                sndAssistEven.append([])

#             print evenGoalsNumber
#             print evenGoals
        #     print evenFstNumber
        #     print evenSndNumber
#             print evenGoalTeam
        #     print evenarrayFailure

            for y in range(0,len(evenGoalTeam)):
                goalEven[y].append(evenGoalsNumber[y])
                fstAssistEven[y].append(evenFstNumber[y])
                sndAssistEven[y].append(evenSndNumber[y])


            for y in range(0,len(goalEven)):
                if evenGoalTeam[y]==homeTeam:
                    goalEven[y].insert(0,str(homeTeam))
                    fstAssistEven[y].insert(0,str(homeTeam))
                    sndAssistEven[y].insert(0,str(homeTeam))
                else:
                    goalEven[y].insert(0,str(awayTeam))
                    fstAssistEven[y].insert(0,str(awayTeam))
                    sndAssistEven[y].insert(0,str(awayTeam))

        #     print "goalEven"
        #     print goalEven
        #     print fstAssistEven
        #     print sndAssistEven
    #         print oddGoalTeam
    #         print goalOdd
            for y in range(0,len(goalOdd)):
                if oddGoalTeam[y]==homeTeam:
                    goalOdd[y].insert(0,str(homeTeam))
                    fstAssistOdd[y].insert(0,str(homeTeam))
                    sndAssistOdd[y].insert(0,str(homeTeam))
                else:
                    goalOdd[y].insert(0,str(awayTeam))
                    fstAssistOdd[y].insert(0,str(awayTeam))
                    sndAssistOdd[y].insert(0,str(awayTeam))

        #     print "goalOdd"
        #     print goalOdd
        #     print fstAssistOdd
        #     print sndAssistOdd



        #     print goalEven+goalOdd
        #     print fstAssistEven+fstAssistOdd
        #     print sndAssistEven+sndAssistOdd
            Scorers.append(goalEven+goalOdd)
            FstAssistsPlayers.append(fstAssistEven+fstAssistOdd)
            SndAssistsPlayers.append(sndAssistEven+sndAssistOdd)
            plusMinusPlayers.append(evenArrayTemp+oddArrayTemp)
    elif numGames in [20036,20078,20232,20235,20290,20441,20461,20547,20755,20812,20846,20903,21025,21114,21144,21151,21164,21176]:   
        print numGames
        soup = BeautifulSoup(get_poll_xml1(numGames))
        # soup

        result1= soup.find_all("tr", attrs={"class":"oddColor"} )

        result2=[elem.find_all("td", attrs={"align":"left"} ) for elem in result1]

        resultEven= soup.find_all("tr", attrs={"class":"evenColor"} )

        resultEven=[elem.find_all("td", attrs={"align":"left"} ) for elem in resultEven]

        result3= soup.find_all("td", attrs={"align":"center", "style":"font-size: 40px;font-weight:bold"} )

        totalGoals=sum([int(elem.text.strip()) for elem in result3])
        resultCen=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1]
        if totalGoals%2==0:
            ODDGoals=totalGoals/2
            EVENGoals=totalGoals/2
        else:
            ODDGoals=totalGoals/2+1
            EVENGoals=totalGoals/2

        oddGoals=[]
        oddFstAssists=[]
        oddSndAssists=[]
        oddarrayFailure=[]
        for x in range(0,ODDGoals):
            if len(result2[x])==3:
                oddGoals.append(result2[x][0])
                oddFstAssists.append(result2[x][1])
                oddSndAssists.append(result2[x][2])
            else:
                oddarrayFailure.append(x)

        evenGoals=[]
        evenFstAssists=[]
        evenSndAssists=[]    
        evenarrayFailure=[]
        for x in range(0,EVENGoals):
        #     print "Test"
        #     print 
            if len(resultEven[x])==3:
                evenGoals.append(resultEven[x][0])
        #         print resultEven[x][1]
                evenFstAssists.append(resultEven[x][1])
                evenSndAssists.append(resultEven[x][2])
            else:
                evenarrayFailure.append(x)
        #     else:
        #         evenGoals.append(resultEven[x][0])
        # #         print resultEven[x][1]
        #         evenFstAssists.append(resultEven[x][1])
        #         evenSndAssists.append()



        resultplayers=soup.find_all("font", attrs={"style":"cursor:hand;"} )

        tds=soup.find_all("td" )[1:]
        tds=[str(elem) for elem in tds]

        count=[]
        tds2=[]
    #     print tds

        for x in range(0,len(tds)):
            if "font style=" in tds[x]:
                count.append(tds[x].count ("font style="))
                tds2.append(tds[x])
    #     print tds2[2]
    #     print tds2
        if tds2!=[]:
            indices = [i for i, x in enumerate(tds2[2]) if x == ","]
        #     print tds2[2]
            temp=[]
            for x in range(0,len(indices)):
                if x==0:
                    temp.append(tds2[2][:indices[0]])
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x!=len(indices)-1:
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x==len(indices)-1:
                    temp.append(tds2[2][indices[x]:len(tds2[2])])
    #         print temp
            if temp!=[]:
                temp[0]=temp[0].replace("<td>", "")
        #     print temp

        #     print temp
            for x in range(0,len(temp)):
                temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                temp[x]=temp[x][0:(temp[x].index("<"))] 
            arrayTemp=[]

            indices = []

            arrayTemp=[]
            for y in range(1,len(tds2)):
                temp=[]
                indices = [i for i, x in enumerate(tds2[y]) if x == ","]
            #     print tds2[y]
            #     print indices
                for x in range(0,len(indices)):
                    if x==0:
                        temp.append(tds2[y][:indices[0]])
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x!=len(indices)-1:
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x==len(indices)-1:
                        temp.append(tds2[y][indices[x]:len(tds2[y])])
        #         print y
        #         print temp
                if temp!=[]:
                    temp[0]=temp[0].replace("<td>", "")
            #     print y
            #     print temp
                for x in range(0,len(temp)):
                    temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                    temp[x]=temp[x][0:(temp[x].index("<"))]
                arrayTemp.append(temp)



            resultTeam=[elem.find_all("td", attrs={"align":"left","class":"heading + bborder"} ) for elem in soup]
            homeTeam=resultTeam[0][3].text.strip()[:resultTeam[0][3].text.strip().index(" ")]
            awayTeam=resultTeam[0][4].text.strip()[:resultTeam[0][4].text.strip().index(" ")]
            resultTeam1= soup.find_all("tr", attrs={"class":"oddColor"} )
            resultTeam2=[elem.find_all("td", attrs={"align":"center"} ) for elem in resultTeam1]

            result1TeamEven= soup.find_all("tr", attrs={"class":"evenColor"} )
            result2TeamEven=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1TeamEven]
            oddGoalTeam=[]
            evenGoalTeam=[]
        #     print "EVENGoals"
        #     print ODDGoals
        #     print EVENGoals
        #     print arrayTemp
        #     print "evenarrayFailure"
        #     print evenarrayFailure
        #     # oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
        #     # print indicesloc

        #     print arrayTemp
    #         print 
            for x in range(0,ODDGoals):
                if x  not in oddarrayFailure:
                    oddGoalTeam.append(str(resultTeam2[x][4].text.strip()))
#             print evenarrayFailure
            for x in range(0,EVENGoals):
        #         print x
                if x not in evenarrayFailure:
        #             print x
                    evenGoalTeam.append(str(result2TeamEven[x][4].text.strip()))

            indicesloc = [i for i, x in enumerate(arrayTemp) if x == []]
            # print arrayTemp.index([])
        #     print indicesloc 
            # indicesloc=[]
            indicesloc= [ elem/2  for elem in indicesloc if elem%2==0]
        #     print "result2TeamEven[indicesloc[0]]"
        #     print indicesloc
        #     print result2TeamEven[0]
        #     print result2TeamEven[1]
        #     print result2TeamEven[2]
        #     print result2TeamEven[3]
        #     print result2TeamEven[4]
        #     print result2TeamEven[5]
        #     print "result2TeamEven[indicesloc[0]/2]"
            # print result2TeamEven[indicesloc[0]/2]

            # print result2TeamEven
    #         print indicesloc
    #         print totalGoals
            # print result2TeamEven[indicesloc[0]]
    #         print evenGoalTeam
    #         for x in range(0,len(indicesloc)):
    # #             print x
    # #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
    #             if totalGoals%2==0:
    #                 print "Even!"
    #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    # #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    # #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals  and indicesloc[x]!=totalGoals-1):
    #             elif totalGoals%2==1:
    #                 print "Odd!"
    # #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    # #         print indicesloc
    # #         print totalGoals
    # #         print evenGoalTeam
    #         [1]
    # 3
    # []
            oddArrayTemp=[]
            evenArrayTemp=[]
            for y in range(0,len(arrayTemp)):
                if y%4==1:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==0:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==2:
                    evenArrayTemp.append(arrayTemp[y]) 
                elif y%4==3:
                    evenArrayTemp.append(arrayTemp[y])
        #     print "oddArrayTemp"   
            # print arrayTemp.index([])

        #     print oddGoalTeam
        #     print evenGoalTeam
        #     print oddArrayTemp
        #     for y in range(0,len(oddArrayTemp)/2):
        #         if oddGoalTeam[y]==homeTeam:
        #             oddArrayTemp[2*y].append("W")
        #             oddArrayTemp[2*y+1].append("L")
        #         else:
        #             oddArrayTemp[2*y].append("L")
        #             oddArrayTemp[2*y+1].append("W")

        #     print evenArrayTemp
        #     print evenGoalTeam
        #     print evenarrayFailure
        #     print len(evenArrayTemp)
        #     print arrayTemp
        #     print len(evenArrayTemp)/2
        #     print len(evenGoalTeam)
        #     print evenGoalTeam
            evenArrayTemp=filter(lambda a: a != [], evenArrayTemp)
            oddArrayTemp=filter(lambda a: a != [], oddArrayTemp)
            # evenArrayTemp.remove([])
        #     print evenArrayTemp
    #         print oddGoalTeam
    #         print oddArrayTemp
    #         print evenGoalTeam
    #         print evenArrayTemp
            for y in range(0,len(oddArrayTemp)/2):
                if oddGoalTeam[y]==homeTeam:
                    oddArrayTemp[2*y].insert(0,"W")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"L")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    oddArrayTemp[2*y].insert(0,"L")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"W")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
    #         print evenArrayTemp
    #         print evenGoalTeam

            for y in range(0,len(evenArrayTemp)/2):
                if evenGoalTeam[y]==homeTeam:
                    evenArrayTemp[2*y].insert(0,"W")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"L")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    evenArrayTemp[2*y].insert(0,"L")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"W")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)

        #     for y in range(0,len(evenArrayTemp)/2):
        #     #     print y
        #         if evenGoalTeam[y]==homeTeam:
        #             evenArrayTemp[2*y].append("W")
        #             evenArrayTemp[2*y+1].append("L")
        #         else:
        #             evenArrayTemp[2*y].append("L")
        #             evenArrayTemp[2*y+1].append("W")

        #     print 
        #     print result2[1]
        #     print result2[2]
        #     print result2[3]
        #     print indicesloc
    #         print EVENGoals
    #         print result2[0]
    #         print result2[1]
    #         print result2[2]
    #         print result2[3]
    #         print totalGoals
    #         print indicesloc
            print result2[EVENGoals]
    #         if len(resultEven[x])==3:
            for x in range(0,len(indicesloc)):
            #     print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0:
            #         evenGoalTeam.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
    #                 evenGoals.append(result2[EVENGoals][0])
    #                 evenFstAssists.append(result2[EVENGoals][1])
    #                 evenSndAssists.append(result2[EVENGoals][2])
                    if len(result2[ODDGoals])==3:
                        oddGoals.append(result2[ODDGoals][0])
                        oddFstAssists.append(result2[ODDGoals][1])
                        oddSndAssists.append(result2[ODDGoals][2])
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
            #         oddGoalTeam.append((str(resultTeam2[indicesloc[x]][4].text.strip())))
    #                 oddGoals.append(result2[ODDGoals][0])
    #                 oddFstAssists.append(result2[ODDGoals][1])
    #                 oddSndAssists.append(result2[ODDGoals][2])
#                     print "Yeah"
#                     print EVENGoals
#                     print result2TeamEven[0]
#                     print result2TeamEven[1]
#                     print result2TeamEven[2]
#                     print " result2TeamEven[3]"
#                     print result2TeamEven[3]
#                     print result2[ODDGoals]
#                     print len(result2TeamEven[EVENGoals])
                    if len(resultEven[EVENGoals])==3:
#                         print "Yeah1"
                        evenGoals.append(resultEven[EVENGoals][0])
                        evenFstAssists.append(resultEven[EVENGoals][1])
                        evenSndAssists.append(resultEven[EVENGoals][2])
            if totalGoals1%2==0:
                strtemp=str(resultCen[EVENGoals1][1])[(str(resultCen[EVENGoals1][1]).index(">"))+1:]
                strtemp=strtemp[0:(strtemp.index("<"))] 
                manPower=str(resultCen[EVENGoals1][3])[(str(resultCen[EVENGoals1][3]).index(">"))+1:]
                manPower=manPower[0:(manPower.index("<"))] 
            else:
                strtemp=str(resultCen[ODDGoals1][1])[(str(resultCen[ODDGoals1][1]).index(">"))+1:]
                strtemp=strtemp[0:(strtemp.index("<"))]
                manPower=str(resultCen[ODDGoals1][3])[(str(resultCen[ODDGoals1][3]).index(">"))+1:]
                manPower=manPower[0:(manPower.index("<"))] 
            # oddGoals.append(result2[ODDGoals][0])
            # oddFstAssists.append(result2[ODDGoals][1])
            # oddSndAssists.append(result2[ODDGoals][2])

            oddGoalsNumber= [str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddGoals]
            oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
            oddSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddSndAssists]
            evenGoalsNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenGoals]
            evenFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenFstAssists]
            evenSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenSndAssists ]
        #     print "evenGoalsNumber"
        #     print oddGoals
            # for x in range(0,len(indicesloc)):
            #     print x
            #     if indicesloc[x]%2==0:
            #         evenGoalsNumber.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
            #     else:
            #         oddGoalsNumber.append((str(resultTeam2[indicesloc[x]][4].text.strip())))

            goalOdd = []
            fstAssistOdd = []
            sndAssistOdd = []

            for y in range(0,len(oddGoalTeam)):
                goalOdd.append([])
                fstAssistOdd.append([])
                sndAssistOdd.append([])
#             print oddGoalsNumber
        #     print oddFstNumber
        #     print oddSndNumber
#             print oddGoalTeam

            for y in range(0,len(oddGoalTeam)):
                goalOdd[y].append(oddGoalsNumber[y])
                fstAssistOdd[y].append(oddFstNumber[y])
                sndAssistOdd[y].append(oddSndNumber[y])

            goalEven = []
            fstAssistEven = []
            sndAssistEven = []

            for y in range(0,len(evenGoalTeam)):
                goalEven.append([])
                fstAssistEven.append([])
                sndAssistEven.append([])

#             print evenGoalsNumber
#             print evenGoals
        #     print evenFstNumber
        #     print evenSndNumber
#             print evenGoalTeam
        #     print evenarrayFailure

            for y in range(0,len(evenGoalTeam)):
                goalEven[y].append(evenGoalsNumber[y])
                fstAssistEven[y].append(evenFstNumber[y])
                sndAssistEven[y].append(evenSndNumber[y])


            for y in range(0,len(goalEven)):
                if evenGoalTeam[y]==homeTeam:
                    goalEven[y].insert(0,str(homeTeam))
                    fstAssistEven[y].insert(0,str(homeTeam))
                    sndAssistEven[y].insert(0,str(homeTeam))
                else:
                    goalEven[y].insert(0,str(awayTeam))
                    fstAssistEven[y].insert(0,str(awayTeam))
                    sndAssistEven[y].insert(0,str(awayTeam))

        #     print "goalEven"
        #     print goalEven
        #     print fstAssistEven
        #     print sndAssistEven
    #         print oddGoalTeam
    #         print goalOdd
            for y in range(0,len(goalOdd)):
                if oddGoalTeam[y]==homeTeam:
                    goalOdd[y].insert(0,str(homeTeam))
                    fstAssistOdd[y].insert(0,str(homeTeam))
                    sndAssistOdd[y].insert(0,str(homeTeam))
                else:
                    goalOdd[y].insert(0,str(awayTeam))
                    fstAssistOdd[y].insert(0,str(awayTeam))
                    sndAssistOdd[y].insert(0,str(awayTeam))

#             print "evenOdd"
#             print goalEven
        #     print fstAssistOdd
        #     print sndAssistOddresultEven



        #     print goalEven+goalOdd
        #     print fstAssistEven+fstAssistOdd
        #     print sndAssistEven+sndAssistOdd
            print "strtempYeah"
            print strtemp
            print resultCen[ODDGoals1][1]
            Goal=goalEven+goalOdd
            FstAssist=fstAssistEven+fstAssistOdd
            SndAssist=sndAssistEven+sndAssistOdd
            ArrayTemp=evenArrayTemp+oddArrayTemp
            if strtemp=="SO":
                del ArrayTemp[-1]
                del FstAssist[-1]
                del SndAssist[-1]
                del Goal[-1]
            Scorers.append(Goal)
            FstAssistsPlayers.append(FstAssist)
            SndAssistsPlayers.append(SndAssist)
            plusMinusPlayers.append(ArrayTemp)
print Scorers
newScorers=[]
for x in range(0,len(Scorers)):
    newScorers=newScorers+Scorers[x]
print newScorers
newFstAssistsPlayers=[]
for x in range(0,len(FstAssistsPlayers)):
    newFstAssistsPlayers=newFstAssistsPlayers+FstAssistsPlayers[x]
print newFstAssistsPlayers
newSndAssistsPlayers=[]
for x in range(0,len(SndAssistsPlayers)):
    newSndAssistsPlayers=newSndAssistsPlayers+SndAssistsPlayers[x]
print newSndAssistsPlayers
print len(newScorers)
print len(newFstAssistsPlayers)
print len(newSndAssistsPlayers)
print FstAssistsPlayers
print SndAssistsPlayers
print len(Scorers)
print len(FstAssistsPlayers)
print len(SndAssistsPlayers)
print plusMinusPlayers
print len(plusMinusPlayers)
print np.unique(newScorers)
# print list(set(zip(*newScorers)[1]))
uniqueNewScorers=[]
for x in range(0,len(newScorers)):
    if newScorers[x] not in uniqueNewScorers:
        uniqueNewScorers.append(newScorers[x])
print uniqueNewScorers
print len(uniqueNewScorers)
sortedUniqueNewScorers= sorted(uniqueNewScorers)
uniqueNewFstAssistsPlayers=[]

for x in range(0,len(newFstAssistsPlayers)):
    if newFstAssistsPlayers[x] not in uniqueNewFstAssistsPlayers:
        uniqueNewFstAssistsPlayers.append(newFstAssistsPlayers[x])

sortedUniqueNewFstAssistsPlayers= sorted(uniqueNewFstAssistsPlayers)

uniqueNewSndAssistsPlayers=[]
for x in range(0,len(newSndAssistsPlayers)):
    if newSndAssistsPlayers[x] not in uniqueNewSndAssistsPlayers:
        uniqueNewSndAssistsPlayers.append(newSndAssistsPlayers[x])

sortedUniqueNewSndAssistsPlayers= sorted(uniqueNewSndAssistsPlayers)

for x in range(0,len(sortedUniqueNewScorers)):
    counter=0
    for y in range(0,len(newScorers)):
        if sortedUniqueNewScorers[x]==newScorers[y]:
            counter=counter+1
    sortedUniqueNewScorers[x].append(counter)
print sortedUniqueNewScorers

for x in range(0,len(sortedUniqueNewFstAssistsPlayers)):
    counter=0
    for y in range(0,len(newFstAssistsPlayers)):
        if sortedUniqueNewFstAssistsPlayers[x]==newFstAssistsPlayers[y]:
            counter=counter+1
    sortedUniqueNewFstAssistsPlayers[x].append(counter)
print sortedUniqueNewFstAssistsPlayers

for x in range(0,len(sortedUniqueNewSndAssistsPlayers)):
    counter=0
    for y in range(0,len(newSndAssistsPlayers)):
        if sortedUniqueNewSndAssistsPlayers[x]==newSndAssistsPlayers[y]:
            counter=counter+1
    sortedUniqueNewSndAssistsPlayers[x].append(counter)
print sortedUniqueNewSndAssistsPlayers


print Scorers
print FstAssistsPlayers
print SndAssistsPlayers
print plusMinusPlayers
# print Scorers


20001
<td align="center">2</td>
strtemp
3
EV
20002
<td align="center">2</td>
strtemp
3
EV
20003
<td align="center">2</td>
strtemp
1
2
20004
<td align="center">2</td>
strtemp
1
2
20005
<td align="center">2</td>
strtemp
1
2
20006
<td align="center">2</td>
strtemp
1
2
20007
Even!
<td align="center">PP</td>
strtemp
3
PP
20008
<td align="center">2</td>
strtemp
SO

20009
<td align="center">2</td>
strtemp
2
PP
20010
<td align="center">2</td>
strtemp
OT
PP
20011
<td align="center">2</td>
strtemp
3
EV
20012
<td align="center">2</td>
strtemp
3
PP
20013
<td align="center">2</td>
strtemp
SO

20014
<td align="center">2</td>
strtemp
2
EV
20015
<td align="center">2</td>
strtemp
3
PP
20016
<td align="center">2</td>
strtemp
1
2
20017
<td align="center">2</td>
strtemp
1
2
20018
<td align="center">2</td>
strtemp
1
2
20019
<td align="center">2</td>
strtemp
3
PP
20020
<td align="center">2</td>
strtemp
3
EV
20021
<td align="center">2</td>
strtemp
SO

20022
<td align="center">2</td>
strtemp
1
2
20023
<td ali

In [2]:

import json
import unicodedata
import numpy as np
import networkx as nx
import requests
from pattern import web
import matplotlib.pyplot as plt

# set some nicer defaults for matplotlib
from matplotlib import rcParams

def get_poll_xml1(poll_id):
    url = "http://www.nhl.com/scores/htmlreports/20142015/GS0%i.HTM" % int(poll_id)
    return requests.get(url
                       ).text

from bs4 import BeautifulSoup
Scorers=[]
Scorers3=[]
FstAssistsPlayers=[]
SndAssistsPlayers=[]
plusMinusPlayers=[]
# [20036,20461,20846,21114,21151,21164,21176]:
# [20036,20149,20235,20332,20461,20742,20846,21114,21151,21164,21176]:
for numGames in range(20001,21231):
    if numGames not in [20036,20078,20149,20232,20235,20290,20332,20441,20461,20547,20742,20755,20812,20846,20903,21025,21114,21144,21151,21164,21176]:
        print numGames
        soup = BeautifulSoup(get_poll_xml1(numGames))
        # soup

        result1= soup.find_all("tr", attrs={"class":"oddColor"} )
#         resultCenter= soup.find_all("td", attrs={"align":"center","class":"oddColor"} )
#         resultCen= result1.find_all("td", attrs={"align":"center"} )
        resultCen=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1]
#         print resultCen
        
        result2=[elem.find_all("td", attrs={"align":"left"} ) for elem in result1]

        resultEven= soup.find_all("tr", attrs={"class":"evenColor"} )

        resultEven=[elem.find_all("td", attrs={"align":"left"} ) for elem in resultEven]

        result3= soup.find_all("td", attrs={"align":"center", "style":"font-size: 40px;font-weight:bold"} )

        totalGoals=sum([int(elem.text.strip()) for elem in result3])

        if totalGoals%2==0:
            ODDGoals=totalGoals/2
            EVENGoals=totalGoals/2
        else:
            ODDGoals=totalGoals/2+1
            EVENGoals=totalGoals/2

        oddGoals=[]
        oddFstAssists=[]
        oddSndAssists=[]
        oddarrayFailure=[]
        for x in range(0,ODDGoals):
            if len(result2[x])==3:
                oddGoals.append(result2[x][0])
                oddFstAssists.append(result2[x][1])
                oddSndAssists.append(result2[x][2])
            else:
                oddarrayFailure.append(x)

        evenGoals=[]
        evenFstAssists=[]
        evenSndAssists=[]    
        evenarrayFailure=[]
        for x in range(0,EVENGoals):
        #     print "Test"
        #     print 
            if len(resultEven[x])==3:
                evenGoals.append(resultEven[x][0])
        #         print resultEven[x][1]
                evenFstAssists.append(resultEven[x][1])
                evenSndAssists.append(resultEven[x][2])
            else:
                evenarrayFailure.append(x)
        #     else:
        #         evenGoals.append(resultEven[x][0])
        # #         print resultEven[x][1]
        #         evenFstAssists.append(resultEven[x][1])
        #         evenSndAssists.append()



        resultplayers=soup.find_all("font", attrs={"style":"cursor:hand;"} )

        tds=soup.find_all("td" )[1:]
        tds=[str(elem) for elem in tds]

        count=[]
        tds2=[]
    #     print tds

        for x in range(0,len(tds)):
            if "font style=" in tds[x]:
                count.append(tds[x].count ("font style="))
                tds2.append(tds[x])
    #     print tds2[2]
    #     print tds2
        if tds2!=[]:
            indices = [i for i, x in enumerate(tds2[2]) if x == ","]
        #     print tds2[2]
            temp=[]
            for x in range(0,len(indices)):
                if x==0:
                    temp.append(tds2[2][:indices[0]])
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x!=len(indices)-1:
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x==len(indices)-1:
                    temp.append(tds2[2][indices[x]:len(tds2[2])])
    #         print temp
            if temp!=[]:
                temp[0]=temp[0].replace("<td>", "")
        #     print temp

        #     print temp
            for x in range(0,len(temp)):
                temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                temp[x]=temp[x][0:(temp[x].index("<"))] 
            arrayTemp=[]

            indices = []

            arrayTemp=[]
            for y in range(1,len(tds2)):
                temp=[]
                indices = [i for i, x in enumerate(tds2[y]) if x == ","]
            #     print tds2[y]
            #     print indices
                for x in range(0,len(indices)):
                    if x==0:
                        temp.append(tds2[y][:indices[0]])
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x!=len(indices)-1:
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x==len(indices)-1:
                        temp.append(tds2[y][indices[x]:len(tds2[y])])
        #         print y
        #         print temp
                if temp!=[]:
                    temp[0]=temp[0].replace("<td>", "")
            #     print y
            #     print temp
                for x in range(0,len(temp)):
                    temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                    temp[x]=temp[x][0:(temp[x].index("<"))]
                arrayTemp.append(temp)



            resultTeam=[elem.find_all("td", attrs={"align":"left","class":"heading + bborder"} ) for elem in soup]
            homeTeam=resultTeam[0][3].text.strip()[:resultTeam[0][3].text.strip().index(" ")]
            awayTeam=resultTeam[0][4].text.strip()[:resultTeam[0][4].text.strip().index(" ")]
            resultTeam1= soup.find_all("tr", attrs={"class":"oddColor"} )
            resultTeam2=[elem.find_all("td", attrs={"align":"center"} ) for elem in resultTeam1]

            result1TeamEven= soup.find_all("tr", attrs={"class":"evenColor"} )
            result2TeamEven=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1TeamEven]
            oddGoalTeam=[]
            evenGoalTeam=[]
        #     print "EVENGoals"
        #     print ODDGoals
        #     print EVENGoals
        #     print arrayTemp
#             print "evenarrayFailure"
#             print evenarrayFailure
        #     # oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
        #     # print indicesloc

        #     print arrayTemp
    #         print 
            for x in range(0,ODDGoals):
                if x  not in oddarrayFailure:
                    oddGoalTeam.append(str(resultTeam2[x][4].text.strip()))
#             print evenarrayFailure
            for x in range(0,EVENGoals):
        #         print x
                if x not in evenarrayFailure:
        #             print x
                    evenGoalTeam.append(str(result2TeamEven[x][4].text.strip()))

            indicesloc = [i for i, x in enumerate(arrayTemp) if x == []]
            # print arrayTemp.index([])
        #     print indicesloc 
            # indicesloc=[]
            indicesloc= [ elem/2  for elem in indicesloc if elem%2==0]
        #     print "result2TeamEven[indicesloc[0]]"
        #     print indicesloc
        #     print result2TeamEven[0]
        #     print result2TeamEven[1]
        #     print result2TeamEven[2]
        #     print result2TeamEven[3]
        #     print result2TeamEven[4]
        #     print result2TeamEven[5]
        #     print "result2TeamEven[indicesloc[0]/2]"
            # print result2TeamEven[indicesloc[0]/2]

            # print result2TeamEven
    #         print indicesloc
    #         print totalGoals
            # print result2TeamEven[indicesloc[0]]
    #         print evenGoalTeam
#             print "result2[0]"
#             print result2[0]
#             print result2[1]
#             print result2[2]
            
            totalGoals1=totalGoals
            for x in range(0,len(indicesloc)):
    #             print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                totalGoals1=totalGoals1+1
                if totalGoals%2==0:
                    print "Even!"
                    oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals  and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
                    print "Odd!"
    #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
                    evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #         print indicesloc
    #         print totalGoals
    #         print evenGoalTeam
            if totalGoals%2==0:
                ODDGoals1=totalGoals1/2
                EVENGoals1=totalGoals1/2
            else:
                ODDGoals1=totalGoals1/2+1
                EVENGoals1=totalGoals1/2
#             print "resultCen[totalGoals1]"
#             print resultCen[EVENGoals1][2]
#             print resultCen[ODDGoals1][2]
#             print resultCen[EVENGoals1][1]
#             print resultCen[ODDGoals1][1]
#             print resultCen[EVENGoals1][0]
            resultCenEVENGoals1=str(resultCen[EVENGoals1][1])
#             print resultCenEVENGoals1[(resultCenEVENGoals1.index(">")+1):len(resultCenEVENGoals1)]
#             print str(resultCen[EVENGoals1][1])
#             print str(resultCen[EVENGoals1][1])[(str(resultCen[EVENGoals1][1]).index(">")+1):]
            if totalGoals1%2==1:
                strtemp=str(resultCen[EVENGoals1][1])[(str(resultCen[EVENGoals1][1]).index(">"))+1:]
                strtemp=strtemp[0:(strtemp.index("<"))] 
                manPower=str(resultCen[EVENGoals1][3])[(str(resultCen[EVENGoals1][3]).index(">"))+1:]
                manPower=manPower[0:(manPower.index("<"))] 
            else:
                strtemp=str(resultCen[ODDGoals1][1])[(str(resultCen[ODDGoals1][1]).index(">"))+1:]
                strtemp=strtemp[0:(strtemp.index("<"))]
                manPower=str(resultCen[ODDGoals1][3])[(str(resultCen[ODDGoals1][3]).index(">"))+1:]
                manPower=manPower[0:(manPower.index("<"))] 
#             print strtemp
            print resultCen[ODDGoals1][3]
            
#         <td align="center">SO</td>
#             temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
#                 temp[x]=temp[x][0:(temp[x].index("<"))] 

#             print resultCen[ODDGoals1][0]
            
                
    #         [1]
    # 3
    # []
            oddArrayTemp=[]
            evenArrayTemp=[]
            for y in range(0,len(arrayTemp)):
                if y%4==1:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==0:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==2:
                    evenArrayTemp.append(arrayTemp[y]) 
                elif y%4==3:
                    evenArrayTemp.append(arrayTemp[y])
        #     print "oddArrayTemp"   
            # print arrayTemp.index([])

        #     print oddGoalTeam
        #     print evenGoalTeam
        #     print oddArrayTemp
        #     for y in range(0,len(oddArrayTemp)/2):
        #         if oddGoalTeam[y]==homeTeam:
        #             oddArrayTemp[2*y].append("W")
        #             oddArrayTemp[2*y+1].append("L")
        #         else:
        #             oddArrayTemp[2*y].append("L")
        #             oddArrayTemp[2*y+1].append("W")

        #     print evenArrayTemp
        #     print evenGoalTeam
        #     print evenarrayFailure
        #     print len(evenArrayTemp)
        #     print arrayTemp
        #     print len(evenArrayTemp)/2
        #     print len(evenGoalTeam)
        #     print evenGoalTeam
            evenArrayTemp=filter(lambda a: a != [], evenArrayTemp)
            oddArrayTemp=filter(lambda a: a != [], oddArrayTemp)
            # evenArrayTemp.remove([])
        #     print evenArrayTemp
    #         print oddGoalTeam
    #         print oddArrayTemp
    #         print evenGoalTeam
    #         print evenArrayTemp
            for y in range(0,len(oddArrayTemp)/2):
                if oddGoalTeam[y]==homeTeam:
                    oddArrayTemp[2*y].insert(0,"W")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"L")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    oddArrayTemp[2*y].insert(0,"L")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"W")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
    #         print evenArrayTemp
    #         print evenGoalTeam

            for y in range(0,len(evenArrayTemp)/2):
                if evenGoalTeam[y]==homeTeam:
                    evenArrayTemp[2*y].insert(0,"W")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"L")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    evenArrayTemp[2*y].insert(0,"L")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"W")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)

        #     for y in range(0,len(evenArrayTemp)/2):
        #     #     print y
        #         if evenGoalTeam[y]==homeTeam:
        #             evenArrayTemp[2*y].append("W")
        #             evenArrayTemp[2*y+1].append("L")
        #         else:
        #             evenArrayTemp[2*y].append("L")
        #             evenArrayTemp[2*y+1].append("W")

        #     print 
        #     print result2[1]
        #     print result2[2]
        #     print result2[3]
        #     print indicesloc
    #         print totalGoals
    #         print indicesloc
            for x in range(0,len(indicesloc)):
            #     print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0:
            #         evenGoalTeam.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
    #                 evenGoals.append(result2[EVENGoals][0])
    #                 evenFstAssists.append(result2[EVENGoals][1])
    #                 evenSndAssists.append(result2[EVENGoals][2])
                    if len(result2[ODDGoals])==3:
                        oddGoals.append(result2[ODDGoals][0])
                        oddFstAssists.append(result2[ODDGoals][1])
                        oddSndAssists.append(result2[ODDGoals][2])
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
            #         oddGoalTeam.append((str(resultTeam2[indicesloc[x]][4].text.strip())))
    #                 oddGoals.append(result2[ODDGoals][0])
    #                 oddFstAssists.append(result2[ODDGoals][1])
    #                 oddSndAssists.append(result2[ODDGoals][2])
#                     print resultEven
                    if len(resultEven[EVENGoals])==3:
                        evenGoals.append(resultEven[EVENGoals][0])
                        evenFstAssists.append(resultEven[EVENGoals][1])
                        evenSndAssists.append(resultEven[EVENGoals][2])

            # oddGoals.append(result2[ODDGoals][0])
            # oddFstAssists.append(result2[ODDGoals][1])
            # oddSndAssists.append(result2[ODDGoals][2])

            oddGoalsNumber= [str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddGoals]
            oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
            oddSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddSndAssists]
            evenGoalsNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenGoals]
            evenFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenFstAssists]
            evenSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenSndAssists ]
        #     print "evenGoalsNumber"
        #     print oddGoals
            # for x in range(0,len(indicesloc)):
            #     print x
            #     if indicesloc[x]%2==0:
            #         evenGoalsNumber.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
            #     else:
            #         oddGoalsNumber.append((str(resultTeam2[indicesloc[x]][4].text.strip())))

            goalOdd = []
            fstAssistOdd = []
            sndAssistOdd = []

            for y in range(0,len(oddGoalTeam)):
                goalOdd.append([])
                fstAssistOdd.append([])
                sndAssistOdd.append([])
        #     print oddGoalsNumber
        #     print oddFstNumber
        #     print oddSndNumber
        #     print oddGoalTeam
            for y in range(0,len(oddGoalTeam)):
                goalOdd[y].append(oddGoalsNumber[y])
                fstAssistOdd[y].append(oddFstNumber[y])
                sndAssistOdd[y].append(oddSndNumber[y])

            goalEven = []
            fstAssistEven = []
            sndAssistEven = []

            for y in range(0,len(evenGoalTeam)):
                goalEven.append([])
                fstAssistEven.append([])
                sndAssistEven.append([])

#             print evenGoalsNumber
        #     print evenFstNumber
        #     print evenSndNumber
#             print evenGoalTeam
        #     print evenarrayFailure
        
            for y in range(0,len(evenGoalTeam)):
                goalEven[y].append(evenGoalsNumber[y])
                fstAssistEven[y].append(evenFstNumber[y])
                sndAssistEven[y].append(evenSndNumber[y])


            for y in range(0,len(goalEven)):
                if evenGoalTeam[y]==homeTeam:
                    goalEven[y].insert(0,str(homeTeam))
                    fstAssistEven[y].insert(0,str(homeTeam))
                    sndAssistEven[y].insert(0,str(homeTeam))
                else:
                    goalEven[y].insert(0,str(awayTeam))
                    fstAssistEven[y].insert(0,str(awayTeam))
                    sndAssistEven[y].insert(0,str(awayTeam))

        #     print "goalEven"
        #     print goalEven
        #     print fstAssistEven
        #     print sndAssistEven
    #         print oddGoalTeam
    #         print goalOdd
            for y in range(0,len(goalOdd)):
                if oddGoalTeam[y]==homeTeam:
                    goalOdd[y].insert(0,str(homeTeam))
                    fstAssistOdd[y].insert(0,str(homeTeam))
                    sndAssistOdd[y].insert(0,str(homeTeam))
                else:
                    goalOdd[y].insert(0,str(awayTeam))
                    fstAssistOdd[y].insert(0,str(awayTeam))
                    sndAssistOdd[y].insert(0,str(awayTeam))

        #     print "goalOdd"
        #     print goalOdd
        #     print fstAssistOdd
        #     print sndAssistOdd



        #     print goalEven+goalOdd
        #     print fstAssistEven+fstAssistOdd
        #     print sndAssistEven+sndAssistOdd
#             print "evenArrayTemp+oddArrayTemp"
#             print evenArrayTemp+oddArrayTemp
            Goal=goalEven+goalOdd
            FstAssist=fstAssistEven+fstAssistOdd
            SndAssist=sndAssistEven+sndAssistOdd
            ArrayTemp=evenArrayTemp+oddArrayTemp
            print "strtemp"
            print strtemp
            print manPower
            if manPower=="SH-EN":
                del ArrayTemp[-1]
                del FstAssist[-1]
                del SndAssist[-1]
                del Goal[-1]
            if strtemp=="SO":
                del ArrayTemp[-1]
                del FstAssist[-1]
                del SndAssist[-1]
                del Goal[-1]
            
            Scorers.append(Goal)
            Scorers3.append(Goal)
            FstAssistsPlayers.append(FstAssist)
            SndAssistsPlayers.append(SndAssist)
            plusMinusPlayers.append(ArrayTemp)
#     elif numGames in [20149,20235,20332,20742]:
    elif numGames in [20149,20332,20742]:
        # [20036,20149,20235,20332,20461,20742,20846,21114,21151,21164,21176]:
#             [20149,20235,20332,20742]:
        print numGames
        soup = BeautifulSoup(get_poll_xml1(numGames))
        # soup

        result1= soup.find_all("tr", attrs={"class":"oddColor"} )

        result2=[elem.find_all("td", attrs={"align":"left"} ) for elem in result1]

        resultEven= soup.find_all("tr", attrs={"class":"evenColor"} )

        resultEven=[elem.find_all("td", attrs={"align":"left"} ) for elem in resultEven]

        result3= soup.find_all("td", attrs={"align":"center", "style":"font-size: 40px;font-weight:bold"} )

        totalGoals=sum([int(elem.text.strip()) for elem in result3])

        if totalGoals%2==0:
            ODDGoals=totalGoals/2
            EVENGoals=totalGoals/2
        else:
            ODDGoals=totalGoals/2+1
            EVENGoals=totalGoals/2

        oddGoals=[]
        oddFstAssists=[]
        oddSndAssists=[]
        oddarrayFailure=[]
        for x in range(0,ODDGoals):
            if len(result2[x])==3:
                oddGoals.append(result2[x][0])
                oddFstAssists.append(result2[x][1])
                oddSndAssists.append(result2[x][2])
            else:
                oddarrayFailure.append(x)

        evenGoals=[]
        evenFstAssists=[]
        evenSndAssists=[]    
        evenarrayFailure=[]
        for x in range(0,EVENGoals):
        #     print "Test"
        #     print 
            if len(resultEven[x])==3:
                evenGoals.append(resultEven[x][0])
        #         print resultEven[x][1]
                evenFstAssists.append(resultEven[x][1])
                evenSndAssists.append(resultEven[x][2])
            else:
                evenarrayFailure.append(x)
        #     else:
        #         evenGoals.append(resultEven[x][0])
        # #         print resultEven[x][1]
        #         evenFstAssists.append(resultEven[x][1])
        #         evenSndAssists.append()



        resultplayers=soup.find_all("font", attrs={"style":"cursor:hand;"} )

        tds=soup.find_all("td" )[1:]
        tds=[str(elem) for elem in tds]

        count=[]
        tds2=[]
    #     print tds

        for x in range(0,len(tds)):
            if "font style=" in tds[x]:
                count.append(tds[x].count ("font style="))
                tds2.append(tds[x])
    #     print tds2[2]
    #     print tds2
        if tds2!=[]:
            indices = [i for i, x in enumerate(tds2[2]) if x == ","]
        #     print tds2[2]
            temp=[]
            for x in range(0,len(indices)):
                if x==0:
                    temp.append(tds2[2][:indices[0]])
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x!=len(indices)-1:
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x==len(indices)-1:
                    temp.append(tds2[2][indices[x]:len(tds2[2])])
    #         print temp
            if temp!=[]:
                temp[0]=temp[0].replace("<td>", "")
        #     print temp

        #     print temp
            for x in range(0,len(temp)):
                temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                temp[x]=temp[x][0:(temp[x].index("<"))] 
            arrayTemp=[]

            indices = []

            arrayTemp=[]
            for y in range(1,len(tds2)):
                temp=[]
                indices = [i for i, x in enumerate(tds2[y]) if x == ","]
            #     print tds2[y]
            #     print indices
                for x in range(0,len(indices)):
                    if x==0:
                        temp.append(tds2[y][:indices[0]])
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x!=len(indices)-1:
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x==len(indices)-1:
                        temp.append(tds2[y][indices[x]:len(tds2[y])])
        #         print y
        #         print temp
                if temp!=[]:
                    temp[0]=temp[0].replace("<td>", "")
            #     print y
            #     print temp
                for x in range(0,len(temp)):
                    temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                    temp[x]=temp[x][0:(temp[x].index("<"))]
                arrayTemp.append(temp)



            resultTeam=[elem.find_all("td", attrs={"align":"left","class":"heading + bborder"} ) for elem in soup]
            homeTeam=resultTeam[0][3].text.strip()[:resultTeam[0][3].text.strip().index(" ")]
            awayTeam=resultTeam[0][4].text.strip()[:resultTeam[0][4].text.strip().index(" ")]
            resultTeam1= soup.find_all("tr", attrs={"class":"oddColor"} )
            resultTeam2=[elem.find_all("td", attrs={"align":"center"} ) for elem in resultTeam1]

            result1TeamEven= soup.find_all("tr", attrs={"class":"evenColor"} )
            result2TeamEven=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1TeamEven]
            oddGoalTeam=[]
            evenGoalTeam=[]
        #     print "EVENGoals"
        #     print ODDGoals
        #     print EVENGoals
        #     print arrayTemp
        #     print "evenarrayFailure"
        #     print evenarrayFailure
        #     # oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
        #     # print indicesloc

        #     print arrayTemp
    #         print 
            for x in range(0,ODDGoals):
                if x  not in oddarrayFailure:
                    oddGoalTeam.append(str(resultTeam2[x][4].text.strip()))
            print evenarrayFailure
            for x in range(0,EVENGoals):
        #         print x
                if x not in evenarrayFailure:
        #             print x
                    evenGoalTeam.append(str(result2TeamEven[x][4].text.strip()))

            indicesloc = [i for i, x in enumerate(arrayTemp) if x == []]
            # print arrayTemp.index([])
        #     print indicesloc 
            # indicesloc=[]
            indicesloc= [ elem/2  for elem in indicesloc if elem%2==0]
        #     print "result2TeamEven[indicesloc[0]]"
        #     print indicesloc
        #     print result2TeamEven[0]
        #     print result2TeamEven[1]
        #     print result2TeamEven[2]
        #     print result2TeamEven[3]
        #     print result2TeamEven[4]
        #     print result2TeamEven[5]
        #     print "result2TeamEven[indicesloc[0]/2]"
            # print result2TeamEven[indicesloc[0]/2]

            # print result2TeamEven
    #         print indicesloc
    #         print totalGoals
            # print result2TeamEven[indicesloc[0]]
    #         print evenGoalTeam
            for x in range(0,len(indicesloc)):
    #             print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0 and (indicesloc[x]!=totalGoals or indicesloc[x]!=totalGoals-1):
                    print "Even!"
                    oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals  and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1 and (indicesloc[x]!=totalGoals or indicesloc[x]!=totalGoals-1):
                    print "Odd!"
    #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
                    evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    #         print indicesloc
    #         print totalGoals
    #         print evenGoalTeam
    #         [1]
    # 3
    # []
            oddArrayTemp=[]
            evenArrayTemp=[]
            for y in range(0,len(arrayTemp)):
                if y%4==1:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==0:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==2:
                    evenArrayTemp.append(arrayTemp[y]) 
                elif y%4==3:
                    evenArrayTemp.append(arrayTemp[y])
        #     print "oddArrayTemp"   
            # print arrayTemp.index([])

        #     print oddGoalTeam
        #     print evenGoalTeam
        #     print oddArrayTemp
        #     for y in range(0,len(oddArrayTemp)/2):
        #         if oddGoalTeam[y]==homeTeam:
        #             oddArrayTemp[2*y].append("W")
        #             oddArrayTemp[2*y+1].append("L")
        #         else:
        #             oddArrayTemp[2*y].append("L")
        #             oddArrayTemp[2*y+1].append("W")

        #     print evenArrayTemp
        #     print evenGoalTeam
        #     print evenarrayFailure
        #     print len(evenArrayTemp)
        #     print arrayTemp
        #     print len(evenArrayTemp)/2
        #     print len(evenGoalTeam)
        #     print evenGoalTeam
            evenArrayTemp=filter(lambda a: a != [], evenArrayTemp)
            oddArrayTemp=filter(lambda a: a != [], oddArrayTemp)
            # evenArrayTemp.remove([])
        #     print evenArrayTemp
    #         print oddGoalTeam
    #         print oddArrayTemp
    #         print evenGoalTeam
    #         print evenArrayTemp
            for y in range(0,len(oddArrayTemp)/2):
                if oddGoalTeam[y]==homeTeam:
                    oddArrayTemp[2*y].insert(0,"W")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"L")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    oddArrayTemp[2*y].insert(0,"L")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"W")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
    #         print evenArrayTemp
    #         print evenGoalTeam

            for y in range(0,len(evenArrayTemp)/2):
                if evenGoalTeam[y]==homeTeam:
                    evenArrayTemp[2*y].insert(0,"W")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"L")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    evenArrayTemp[2*y].insert(0,"L")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"W")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)

        #     for y in range(0,len(evenArrayTemp)/2):
        #     #     print y
        #         if evenGoalTeam[y]==homeTeam:
        #             evenArrayTemp[2*y].append("W")
        #             evenArrayTemp[2*y+1].append("L")
        #         else:
        #             evenArrayTemp[2*y].append("L")
        #             evenArrayTemp[2*y+1].append("W")

        #     print 
        #     print result2[1]
        #     print result2[2]
        #     print result2[3]
        #     print indicesloc
    #         print EVENGoals
    #         print result2[0]
    #         print result2[1]
    #         print result2[2]
    #         print result2[3]
    #         print totalGoals
    #         print indicesloc
#                 print "result2[0]"
#                 print result2[0]
#                 print result2[1]
#                 print result2[2]
    #         if len(resultEven[x])==3:
            for x in range(0,len(indicesloc)):
            #     print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0:
            #         evenGoalTeam.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
    #                 evenGoals.append(result2[EVENGoals][0])
    #                 evenFstAssists.append(result2[EVENGoals][1])
    #                 evenSndAssists.append(result2[EVENGoals][2])
                    if len(result2[ODDGoals])==3:
                        oddGoals.append(result2[ODDGoals][0])
                        oddFstAssists.append(result2[ODDGoals][1])
                        oddSndAssists.append(result2[ODDGoals][2])
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
            #         oddGoalTeam.append((str(resultTeam2[indicesloc[x]][4].text.strip())))
    #                 oddGoals.append(result2[ODDGoals][0])
    #                 oddFstAssists.append(result2[ODDGoals][1])
    #                 oddSndAssists.append(result2[ODDGoals][2])
#                     print "Yeah"
#                     print EVENGoals
#                     print result2TeamEven[0]
#                     print result2TeamEven[1]
#                     print result2TeamEven[2]
#                     print "resultEven[EVENGoals]"
#                     print resultEven[3]
#                     print resultEven[EVENGoals]
#                     print len(result2TeamEven[EVENGoals])
                    if len(resultEven[EVENGoals])==3:
#                         print "Yeah1"
                        evenGoals.append(resultEven[EVENGoals][0])
                        evenFstAssists.append(resultEven[EVENGoals][1])
                        evenSndAssists.append(resultEven[EVENGoals][2])

            # oddGoals.append(result2[ODDGoals][0])
            # oddFstAssists.append(result2[ODDGoals][1])
            # oddSndAssists.append(result2[ODDGoals][2])

            oddGoalsNumber= [str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddGoals]
            oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
            oddSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddSndAssists]
            evenGoalsNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenGoals]
            evenFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenFstAssists]
            evenSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenSndAssists ]
        #     print "evenGoalsNumber"
        #     print oddGoals
            # for x in range(0,len(indicesloc)):
            #     print x
            #     if indicesloc[x]%2==0:
            #         evenGoalsNumber.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
            #     else:
            #         oddGoalsNumber.append((str(resultTeam2[indicesloc[x]][4].text.strip())))

            goalOdd = []
            fstAssistOdd = []
            sndAssistOdd = []

            for y in range(0,len(oddGoalTeam)):
                goalOdd.append([])
                fstAssistOdd.append([])
                sndAssistOdd.append([])
#             print oddGoalsNumber
        #     print oddFstNumber
        #     print oddSndNumber
#             print oddGoalTeam

            for y in range(0,len(oddGoalTeam)):
                goalOdd[y].append(oddGoalsNumber[y])
                fstAssistOdd[y].append(oddFstNumber[y])
                sndAssistOdd[y].append(oddSndNumber[y])

            goalEven = []
            fstAssistEven = []
            sndAssistEven = []

            for y in range(0,len(evenGoalTeam)):
                goalEven.append([])
                fstAssistEven.append([])
                sndAssistEven.append([])

#             print evenGoalsNumber
#             print evenGoals
        #     print evenFstNumber
        #     print evenSndNumber
#             print evenGoalTeam
        #     print evenarrayFailure

            for y in range(0,len(evenGoalTeam)):
                goalEven[y].append(evenGoalsNumber[y])
                fstAssistEven[y].append(evenFstNumber[y])
                sndAssistEven[y].append(evenSndNumber[y])


            for y in range(0,len(goalEven)):
                if evenGoalTeam[y]==homeTeam:
                    goalEven[y].insert(0,str(homeTeam))
                    fstAssistEven[y].insert(0,str(homeTeam))
                    sndAssistEven[y].insert(0,str(homeTeam))
                else:
                    goalEven[y].insert(0,str(awayTeam))
                    fstAssistEven[y].insert(0,str(awayTeam))
                    sndAssistEven[y].insert(0,str(awayTeam))

        #     print "goalEven"
        #     print goalEven
        #     print fstAssistEven
        #     print sndAssistEven
    #         print oddGoalTeam
    #         print goalOdd
            for y in range(0,len(goalOdd)):
                if oddGoalTeam[y]==homeTeam:
                    goalOdd[y].insert(0,str(homeTeam))
                    fstAssistOdd[y].insert(0,str(homeTeam))
                    sndAssistOdd[y].insert(0,str(homeTeam))
                else:
                    goalOdd[y].insert(0,str(awayTeam))
                    fstAssistOdd[y].insert(0,str(awayTeam))
                    sndAssistOdd[y].insert(0,str(awayTeam))

        #     print "goalOdd"
        #     print goalOdd
        #     print fstAssistOdd
        #     print sndAssistOdd



        #     print goalEven+goalOdd
        #     print fstAssistEven+fstAssistOdd
        #     print sndAssistEven+sndAssistOdd
            Scorers.append(goalEven+goalOdd)
            Scorers3.append(goalEven+goalOdd)
            FstAssistsPlayers.append(fstAssistEven+fstAssistOdd)
            SndAssistsPlayers.append(sndAssistEven+sndAssistOdd)
            plusMinusPlayers.append(evenArrayTemp+oddArrayTemp)
    elif numGames in [20036,20078,20232,20235,20290,20441,20461,20547,20755,20812,20846,20903,21025,21114,21144,21151,21164,21176]:   
        print numGames
        soup = BeautifulSoup(get_poll_xml1(numGames))
        # soup

        result1= soup.find_all("tr", attrs={"class":"oddColor"} )

        result2=[elem.find_all("td", attrs={"align":"left"} ) for elem in result1]

        resultEven= soup.find_all("tr", attrs={"class":"evenColor"} )

        resultEven=[elem.find_all("td", attrs={"align":"left"} ) for elem in resultEven]

        result3= soup.find_all("td", attrs={"align":"center", "style":"font-size: 40px;font-weight:bold"} )

        totalGoals=sum([int(elem.text.strip()) for elem in result3])
        resultCen=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1]
        if totalGoals%2==0:
            ODDGoals=totalGoals/2
            EVENGoals=totalGoals/2
        else:
            ODDGoals=totalGoals/2+1
            EVENGoals=totalGoals/2

        oddGoals=[]
        oddFstAssists=[]
        oddSndAssists=[]
        oddarrayFailure=[]
        for x in range(0,ODDGoals):
            if len(result2[x])==3:
                oddGoals.append(result2[x][0])
                oddFstAssists.append(result2[x][1])
                oddSndAssists.append(result2[x][2])
            else:
                oddarrayFailure.append(x)

        evenGoals=[]
        evenFstAssists=[]
        evenSndAssists=[]    
        evenarrayFailure=[]
        for x in range(0,EVENGoals):
        #     print "Test"
        #     print 
            if len(resultEven[x])==3:
                evenGoals.append(resultEven[x][0])
        #         print resultEven[x][1]
                evenFstAssists.append(resultEven[x][1])
                evenSndAssists.append(resultEven[x][2])
            else:
                evenarrayFailure.append(x)
        #     else:
        #         evenGoals.append(resultEven[x][0])
        # #         print resultEven[x][1]
        #         evenFstAssists.append(resultEven[x][1])
        #         evenSndAssists.append()



        resultplayers=soup.find_all("font", attrs={"style":"cursor:hand;"} )

        tds=soup.find_all("td" )[1:]
        tds=[str(elem) for elem in tds]

        count=[]
        tds2=[]
    #     print tds

        for x in range(0,len(tds)):
            if "font style=" in tds[x]:
                count.append(tds[x].count ("font style="))
                tds2.append(tds[x])
    #     print tds2[2]
    #     print tds2
        if tds2!=[]:
            indices = [i for i, x in enumerate(tds2[2]) if x == ","]
        #     print tds2[2]
            temp=[]
            for x in range(0,len(indices)):
                if x==0:
                    temp.append(tds2[2][:indices[0]])
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x!=len(indices)-1:
                    temp.append(tds2[2][indices[x]:indices[x+1]])
                elif x==len(indices)-1:
                    temp.append(tds2[2][indices[x]:len(tds2[2])])
    #         print temp
            if temp!=[]:
                temp[0]=temp[0].replace("<td>", "")
        #     print temp

        #     print temp
            for x in range(0,len(temp)):
                temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                temp[x]=temp[x][0:(temp[x].index("<"))] 
            arrayTemp=[]

            indices = []

            arrayTemp=[]
            for y in range(1,len(tds2)):
                temp=[]
                indices = [i for i, x in enumerate(tds2[y]) if x == ","]
            #     print tds2[y]
            #     print indices
                for x in range(0,len(indices)):
                    if x==0:
                        temp.append(tds2[y][:indices[0]])
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x!=len(indices)-1:
                        temp.append(tds2[y][indices[x]:indices[x+1]])
                    elif x==len(indices)-1:
                        temp.append(tds2[y][indices[x]:len(tds2[y])])
        #         print y
        #         print temp
                if temp!=[]:
                    temp[0]=temp[0].replace("<td>", "")
            #     print y
            #     print temp
                for x in range(0,len(temp)):
                    temp[x]=temp[x][(temp[x].index(">")+1):len(temp[x])]
                    temp[x]=temp[x][0:(temp[x].index("<"))]
                arrayTemp.append(temp)



            resultTeam=[elem.find_all("td", attrs={"align":"left","class":"heading + bborder"} ) for elem in soup]
            homeTeam=resultTeam[0][3].text.strip()[:resultTeam[0][3].text.strip().index(" ")]
            awayTeam=resultTeam[0][4].text.strip()[:resultTeam[0][4].text.strip().index(" ")]
            resultTeam1= soup.find_all("tr", attrs={"class":"oddColor"} )
            resultTeam2=[elem.find_all("td", attrs={"align":"center"} ) for elem in resultTeam1]

            result1TeamEven= soup.find_all("tr", attrs={"class":"evenColor"} )
            result2TeamEven=[elem.find_all("td", attrs={"align":"center"} ) for elem in result1TeamEven]
            oddGoalTeam=[]
            evenGoalTeam=[]
        #     print "EVENGoals"
        #     print ODDGoals
        #     print EVENGoals
        #     print arrayTemp
        #     print "evenarrayFailure"
        #     print evenarrayFailure
        #     # oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
        #     # print indicesloc

        #     print arrayTemp
    #         print 
            for x in range(0,ODDGoals):
                if x  not in oddarrayFailure:
                    oddGoalTeam.append(str(resultTeam2[x][4].text.strip()))
#             print evenarrayFailure
            for x in range(0,EVENGoals):
        #         print x
                if x not in evenarrayFailure:
        #             print x
                    evenGoalTeam.append(str(result2TeamEven[x][4].text.strip()))

            indicesloc = [i for i, x in enumerate(arrayTemp) if x == []]
            # print arrayTemp.index([])
        #     print indicesloc 
            # indicesloc=[]
            indicesloc= [ elem/2  for elem in indicesloc if elem%2==0]
        #     print "result2TeamEven[indicesloc[0]]"
        #     print indicesloc
        #     print result2TeamEven[0]
        #     print result2TeamEven[1]
        #     print result2TeamEven[2]
        #     print result2TeamEven[3]
        #     print result2TeamEven[4]
        #     print result2TeamEven[5]
        #     print "result2TeamEven[indicesloc[0]/2]"
            # print result2TeamEven[indicesloc[0]/2]

            # print result2TeamEven
    #         print indicesloc
    #         print totalGoals
            # print result2TeamEven[indicesloc[0]]
    #         print evenGoalTeam
    #         for x in range(0,len(indicesloc)):
    # #             print x
    # #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
    #             if totalGoals%2==0:
    #                 print "Even!"
    #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    # #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    # #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals  and indicesloc[x]!=totalGoals-1):
    #             elif totalGoals%2==1:
    #                 print "Odd!"
    # #                 oddGoalTeam.append((str(resultTeam2[indicesloc[x]/2][4].text.strip())))
    #                 evenGoalTeam.append((str(result2TeamEven[indicesloc[x]/2][4].text.strip())))
    # #         print indicesloc
    # #         print totalGoals
    # #         print evenGoalTeam
    #         [1]
    # 3
    # []
            oddArrayTemp=[]
            evenArrayTemp=[]
            for y in range(0,len(arrayTemp)):
                if y%4==1:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==0:
                    oddArrayTemp.append(arrayTemp[y]) 
                elif y%4==2:
                    evenArrayTemp.append(arrayTemp[y]) 
                elif y%4==3:
                    evenArrayTemp.append(arrayTemp[y])
        #     print "oddArrayTemp"   
            # print arrayTemp.index([])

        #     print oddGoalTeam
        #     print evenGoalTeam
        #     print oddArrayTemp
        #     for y in range(0,len(oddArrayTemp)/2):
        #         if oddGoalTeam[y]==homeTeam:
        #             oddArrayTemp[2*y].append("W")
        #             oddArrayTemp[2*y+1].append("L")
        #         else:
        #             oddArrayTemp[2*y].append("L")
        #             oddArrayTemp[2*y+1].append("W")

        #     print evenArrayTemp
        #     print evenGoalTeam
        #     print evenarrayFailure
        #     print len(evenArrayTemp)
        #     print arrayTemp
        #     print len(evenArrayTemp)/2
        #     print len(evenGoalTeam)
        #     print evenGoalTeam
            evenArrayTemp=filter(lambda a: a != [], evenArrayTemp)
            oddArrayTemp=filter(lambda a: a != [], oddArrayTemp)
            # evenArrayTemp.remove([])
        #     print evenArrayTemp
    #         print oddGoalTeam
    #         print oddArrayTemp
    #         print evenGoalTeam
    #         print evenArrayTemp
            for y in range(0,len(oddArrayTemp)/2):
                if oddGoalTeam[y]==homeTeam:
                    oddArrayTemp[2*y].insert(0,"W")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"L")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    oddArrayTemp[2*y].insert(0,"L")
                    oddArrayTemp[2*y].insert(0,homeTeam)
                    oddArrayTemp[2*y+1].insert(0,"W")
                    oddArrayTemp[2*y+1].insert(0,awayTeam)
    #         print evenArrayTemp
    #         print evenGoalTeam

            for y in range(0,len(evenArrayTemp)/2):
                if evenGoalTeam[y]==homeTeam:
                    evenArrayTemp[2*y].insert(0,"W")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"L")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)
                else:
                    evenArrayTemp[2*y].insert(0,"L")
                    evenArrayTemp[2*y].insert(0,homeTeam)
                    evenArrayTemp[2*y+1].insert(0,"W")
                    evenArrayTemp[2*y+1].insert(0,awayTeam)

        #     for y in range(0,len(evenArrayTemp)/2):
        #     #     print y
        #         if evenGoalTeam[y]==homeTeam:
        #             evenArrayTemp[2*y].append("W")
        #             evenArrayTemp[2*y+1].append("L")
        #         else:
        #             evenArrayTemp[2*y].append("L")
        #             evenArrayTemp[2*y+1].append("W")

        #     print 
        #     print result2[1]
        #     print result2[2]
        #     print result2[3]
        #     print indicesloc
    #         print EVENGoals
    #         print result2[0]
    #         print result2[1]
    #         print result2[2]
    #         print result2[3]
    #         print totalGoals
    #         print indicesloc
            print result2[EVENGoals]
    #         if len(resultEven[x])==3:
            for x in range(0,len(indicesloc)):
            #     print x
    #             if totalGoals%2==0 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                if totalGoals%2==0:
            #         evenGoalTeam.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
    #                 evenGoals.append(result2[EVENGoals][0])
    #                 evenFstAssists.append(result2[EVENGoals][1])
    #                 evenSndAssists.append(result2[EVENGoals][2])
                    if len(result2[ODDGoals])==3:
                        oddGoals.append(result2[ODDGoals][0])
                        oddFstAssists.append(result2[ODDGoals][1])
                        oddSndAssists.append(result2[ODDGoals][2])
    #             elif totalGoals%2==1 and (indicesloc[x]!=totalGoals and indicesloc[x]!=totalGoals-1):
                elif totalGoals%2==1:
            #         oddGoalTeam.append((str(resultTeam2[indicesloc[x]][4].text.strip())))
    #                 oddGoals.append(result2[ODDGoals][0])
    #                 oddFstAssists.append(result2[ODDGoals][1])
    #                 oddSndAssists.append(result2[ODDGoals][2])
#                     print "Yeah"
#                     print EVENGoals
#                     print result2TeamEven[0]
#                     print result2TeamEven[1]
#                     print result2TeamEven[2]
#                     print " result2TeamEven[3]"
#                     print result2TeamEven[3]
#                     print result2[ODDGoals]
#                     print len(result2TeamEven[EVENGoals])
                    if len(resultEven[EVENGoals])==3:
#                         print "Yeah1"
                        evenGoals.append(resultEven[EVENGoals][0])
                        evenFstAssists.append(resultEven[EVENGoals][1])
                        evenSndAssists.append(resultEven[EVENGoals][2])
            if totalGoals1%2==0:
                strtemp=str(resultCen[EVENGoals1][1])[(str(resultCen[EVENGoals1][1]).index(">"))+1:]
                strtemp=strtemp[0:(strtemp.index("<"))] 
                manPower=str(resultCen[EVENGoals1][3])[(str(resultCen[EVENGoals1][3]).index(">"))+1:]
                manPower=manPower[0:(manPower.index("<"))] 
            else:
                strtemp=str(resultCen[ODDGoals1][1])[(str(resultCen[ODDGoals1][1]).index(">"))+1:]
                strtemp=strtemp[0:(strtemp.index("<"))]
                manPower=str(resultCen[ODDGoals1][3])[(str(resultCen[ODDGoals1][3]).index(">"))+1:]
                manPower=manPower[0:(manPower.index("<"))] 
            # oddGoals.append(result2[ODDGoals][0])
            # oddFstAssists.append(result2[ODDGoals][1])
            # oddSndAssists.append(result2[ODDGoals][2])

            oddGoalsNumber= [str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddGoals]
            oddFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddFstAssists]
            oddSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in oddSndAssists]
            evenGoalsNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenGoals]
            evenFstNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenFstAssists]
            evenSndNumber=[str(elem.text.strip())[0:str(elem.text.strip()).index(" ")] if " " in str(elem.text.strip()) else str(elem.text.strip()) for elem in evenSndAssists ]
        #     print "evenGoalsNumber"
        #     print oddGoals
            # for x in range(0,len(indicesloc)):
            #     print x
            #     if indicesloc[x]%2==0:
            #         evenGoalsNumber.append((str(result2TeamEven[indicesloc[x]][4].text.strip())))
            #     else:
            #         oddGoalsNumber.append((str(resultTeam2[indicesloc[x]][4].text.strip())))

            goalOdd = []
            fstAssistOdd = []
            sndAssistOdd = []

            for y in range(0,len(oddGoalTeam)):
                goalOdd.append([])
                fstAssistOdd.append([])
                sndAssistOdd.append([])
#             print oddGoalsNumber
        #     print oddFstNumber
        #     print oddSndNumber
#             print oddGoalTeam

            for y in range(0,len(oddGoalTeam)):
                goalOdd[y].append(oddGoalsNumber[y])
                fstAssistOdd[y].append(oddFstNumber[y])
                sndAssistOdd[y].append(oddSndNumber[y])

            goalEven = []
            fstAssistEven = []
            sndAssistEven = []

            for y in range(0,len(evenGoalTeam)):
                goalEven.append([])
                fstAssistEven.append([])
                sndAssistEven.append([])

#             print evenGoalsNumber
#             print evenGoals
        #     print evenFstNumber
        #     print evenSndNumber
#             print evenGoalTeam
        #     print evenarrayFailure

            for y in range(0,len(evenGoalTeam)):
                goalEven[y].append(evenGoalsNumber[y])
                fstAssistEven[y].append(evenFstNumber[y])
                sndAssistEven[y].append(evenSndNumber[y])


            for y in range(0,len(goalEven)):
                if evenGoalTeam[y]==homeTeam:
                    goalEven[y].insert(0,str(homeTeam))
                    fstAssistEven[y].insert(0,str(homeTeam))
                    sndAssistEven[y].insert(0,str(homeTeam))
                else:
                    goalEven[y].insert(0,str(awayTeam))
                    fstAssistEven[y].insert(0,str(awayTeam))
                    sndAssistEven[y].insert(0,str(awayTeam))

        #     print "goalEven"
        #     print goalEven
        #     print fstAssistEven
        #     print sndAssistEven
    #         print oddGoalTeam
    #         print goalOdd
            for y in range(0,len(goalOdd)):
                if oddGoalTeam[y]==homeTeam:
                    goalOdd[y].insert(0,str(homeTeam))
                    fstAssistOdd[y].insert(0,str(homeTeam))
                    sndAssistOdd[y].insert(0,str(homeTeam))
                else:
                    goalOdd[y].insert(0,str(awayTeam))
                    fstAssistOdd[y].insert(0,str(awayTeam))
                    sndAssistOdd[y].insert(0,str(awayTeam))

#             print "evenOdd"
#             print goalEven
        #     print fstAssistOdd
        #     print sndAssistOddresultEven



        #     print goalEven+goalOdd
        #     print fstAssistEven+fstAssistOdd
        #     print sndAssistEven+sndAssistOdd
            print "strtempYeah"
            print strtemp
            print resultCen[ODDGoals1][1]
            Goal=goalEven+goalOdd
            FstAssist=fstAssistEven+fstAssistOdd
            SndAssist=sndAssistEven+sndAssistOdd
            ArrayTemp=evenArrayTemp+oddArrayTemp
            if strtemp=="SO":
                del ArrayTemp[-1]
                del FstAssist[-1]
                del SndAssist[-1]
                del Goal[-1]
            Scorers.append(Goal)
            Scorers3.append(Goal)
            FstAssistsPlayers.append(FstAssist)
            SndAssistsPlayers.append(SndAssist)
            plusMinusPlayers.append(ArrayTemp)
print "Scorers1"
import copy
Scorers1=copy.copy(Scorers)
print Scorers
newScorers=[]
# Scorers1=Scorers[:]
print Scorers1
for x in range(0,len(Scorers1)):
    newScorers=newScorers+Scorers1[x]
print newScorers
print "Scorers2"
print Scorers1
print Scorers
newFstAssistsPlayers=[]
for x in range(0,len(FstAssistsPlayers)):
    newFstAssistsPlayers=newFstAssistsPlayers+FstAssistsPlayers[x]
print newFstAssistsPlayers
newSndAssistsPlayers=[]
for x in range(0,len(SndAssistsPlayers)):
    newSndAssistsPlayers=newSndAssistsPlayers+SndAssistsPlayers[x]
print newSndAssistsPlayers
print len(newScorers)
print len(newFstAssistsPlayers)
print len(newSndAssistsPlayers)
print FstAssistsPlayers
print SndAssistsPlayers
print len(Scorers)
print len(FstAssistsPlayers)
print len(SndAssistsPlayers)
print plusMinusPlayers
print len(plusMinusPlayers)
# print np.unique(newScorers)
# print list(set(zip(*newScorers)[1]))
# uniqueNewScorers=[]
# for x in range(0,len(newScorers)):
#     if newScorers[x] not in uniqueNewScorers:
#         uniqueNewScorers.append(newScorers[x])
# print uniqueNewScorers
# print len(uniqueNewScorers)
# sortedUniqueNewScorers= sorted(uniqueNewScorers)

# for x in range(0,len(sortedUniqueNewScorers)):
#     counter=0
#     for y in range(0,len(newScorers)):
#         if sortedUniqueNewScorers[x]==newScorers[y]:
#             counter=counter+1
#     sortedUniqueNewScorers[x].append(counter)

# print sortedUniqueNewScorers
print "Important24"
print FstAssistsPlayers
unassistedGoals=[]
FstassistedGoals=[]
SndassistedGoals=[]
onlyFstassist=[]
SndassistedFstassist=[]


print "Important25"
print FstAssistsPlayers
for x in range(0,len(newScorers)):
    if str(newFstAssistsPlayers[x][1])=='unassisted':
        unassistedGoals.append(newScorers[x])
    else:
        if str(newSndAssistsPlayers[x][1])=='':
            FstassistedGoals.append(newScorers[x])
            onlyFstassist.append(newFstAssistsPlayers[x])
            
        else:
            SndassistedGoals.append(newScorers[x])
            SndassistedFstassist.append(newFstAssistsPlayers[x])
print "Scorers3"
print Scorers1
print Scorers

#             newSndAssistsPlayers
        
print "Important4"
print newScorers
print newFstAssistsPlayers
print newSndAssistsPlayers
print plusMinusPlayers
print "Important5"
print FstAssistsPlayers
# print FstAssistsPlayers1
print newFstAssistsPlayers
print newFstAssistsPlayers[0]
print unassistedGoals
print FstassistedGoals
print SndassistedGoals
print onlyFstassist
print SndassistedFstassist
print newSndAssistsPlayers

uniqueNewScorers=[]
for x in range(0,len(newScorers)):
    if newScorers[x] not in uniqueNewScorers:
        uniqueNewScorers.append(newScorers[x])
print uniqueNewScorers
print len(uniqueNewScorers)
print "Scorers4"
print Scorers1
print Scorers
sortedUniqueNewScorers= sorted(uniqueNewScorers)
print "Scorers5"
print Scorers1
print Scorers


uniqueNewFstAssistsPlayers=[]
# print FstAssistsPlayers
# FstAssistsPlayers1=FstAssistsPlayers
for x in range(0,len(newFstAssistsPlayers)):
    if newFstAssistsPlayers[x] not in uniqueNewFstAssistsPlayers:
        uniqueNewFstAssistsPlayers.append(newFstAssistsPlayers[x])

sortedUniqueNewFstAssistsPlayers= sorted(uniqueNewFstAssistsPlayers)
print "Important23"
print onlyFstassist
print sortedUniqueNewFstAssistsPlayers



uniqueNewSndAssistsPlayers=[]
for x in range(0,len(newSndAssistsPlayers)):
    if newSndAssistsPlayers[x] not in uniqueNewSndAssistsPlayers:
        uniqueNewSndAssistsPlayers.append(newSndAssistsPlayers[x])

sortedUniqueNewSndAssistsPlayers= sorted(uniqueNewSndAssistsPlayers)

uniquePointsPlayers=sortedUniqueNewFstAssistsPlayers[:]
for x in range(0,len(sortedUniqueNewSndAssistsPlayers)):
    if sortedUniqueNewSndAssistsPlayers[x] not in sortedUniqueNewFstAssistsPlayers:
        uniquePointsPlayers.append(sortedUniqueNewSndAssistsPlayers[x])
        
for x in range(0,len(sortedUniqueNewScorers)):
    if sortedUniqueNewScorers[x] not in uniquePointsPlayers:
        uniquePointsPlayers.append(sortedUniqueNewScorers[x])

        
# print uniquePointsPlayers2
print "Scorers6"
print Scorers1
print Scorers
print "Important33"
print sortedUniqueNewFstAssistsPlayers
print sortedUniqueNewSndAssistsPlayers
print sortedUniqueNewScorers
print uniquePointsPlayers

print unassistedGoals
print FstassistedGoals
print SndassistedGoals
print onlyFstassist
print SndassistedFstassist
print newSndAssistsPlayers
uniquePointsPlayers1=uniquePointsPlayers[:]
Scores2=Scorers[:]
# print unassistedGoals[0]
# print uniquePointsPlayers[5]
# print unassistedGoals[0]==uniquePointsPlayers[5]

newplusMinusPlayers=[]
for x in range(0,len(plusMinusPlayers)):
    newplusMinusPlayers=newplusMinusPlayers+plusMinusPlayers[x]
    
    
print newplusMinusPlayers
uniquePointsPlayers2=[]
for x in range(0,50):
    uniquePointsPlayers2.append([])
print "uniquePointsPlayers2"
print uniquePointsPlayers2
print newplusMinusPlayers
print newplusMinusPlayers[0]
# for x in range(0,len(newplusMinusPlayers)):
#     for y in range(2,len(newplusMinusPlayers[x])):
#         uniquePointsPlayers2[x].append("")
# print uniquePointsPlayers2
# uniquePointsPlayers2=[]
for x in range(0,len(newplusMinusPlayers)):
    uniquePointsPlayers2[x].append(newplusMinusPlayers[x][0])
    for y in range(2,len(newplusMinusPlayers[x])):
        uniquePointsPlayers2[x].append(newplusMinusPlayers[x][y])
print uniquePointsPlayers2
arrayUnique2=[]
for x in range(0,len(uniquePointsPlayers2)):
    
    for y in range(2,len(uniquePointsPlayers2[x])):
        unique2=[]
        unique2.append(str(uniquePointsPlayers2[x][0]))
        unique2.append(uniquePointsPlayers2[x][y])
        arrayUnique2.append(unique2)
print "arrayUnique2"
print arrayUnique2
print len(arrayUnique2)
arrayUnique2Store=[]
for x in range(0,len(arrayUnique2)):
    if arrayUnique2[x] not in arrayUnique2Store:
        arrayUnique2Store.append(arrayUnique2[x])

print arrayUnique2Store
print len(arrayUnique2Store)
uniquePointsPlayers1=arrayUnique2Store[:]
uniquePointsPlayers=arrayUnique2Store[:]
#         uniquePointsPlayers2[x].append(plusMinusPlayers[y])
# newplusMinusPlayersWin=newplusMinusPlayers[newplusMinusPlayers[1]=='W']
newplusMinusPlayersWin = [row for row in newplusMinusPlayers if 'W' in row[1]]

temp=newplusMinusPlayersWin[:]
print "Scorers"
print Scorers1
# print Scorers2
print newScorers

print temp
print FstAssistsPlayers
print newSndAssistsPlayers
print newScorers[0][1]
for x in range(0,len(newplusMinusPlayersWin)):
    print x
    temp[x].remove(newScorers[x][1])
    if newFstAssistsPlayers[x][1]!='unassisted' and newFstAssistsPlayers[x][1] in temp[x]:
        temp[x].remove(newFstAssistsPlayers[x][1])
        if newSndAssistsPlayers[x][1]!='' and newSndAssistsPlayers[x][1] in temp[x]:
            temp[x].remove(newSndAssistsPlayers[x][1])
            temp[x].append("secondAssisted")
        else:
            temp[x].append("firstAssisted")
    else:
         temp[x].append("unassisted")
            
print "tem"
firstTemp = [row for row in temp if 'firstAssisted' in row[-1]]
secondTemp = [row for row in temp if 'secondAssisted' in row[-1]]
unassistedTemp = [row for row in temp if 'unassisted' in row[-1]]
print temp
print firstTemp
print secondTemp
print unassistedTemp
print newplusMinusPlayersWin
print "uniquePointsPlayers"
print uniquePointsPlayers
print uniquePointsPlayers1
print FstassistedGoals
arrayfirstTemp=[]
for x in range(0,len(firstTemp)):
    
    for y in range(2,len(firstTemp[x])):
        unique3=[]
        unique3.append(str(firstTemp[x][0]))
        unique3.append(firstTemp[x][y])
        arrayfirstTemp.append(unique3)
print "arrayfirstTemp"
print arrayfirstTemp

arraysecondTemp=[]
for x in range(0,len(secondTemp)):
    
    for y in range(2,len(secondTemp[x])):
        unique3=[]
        unique3.append(str(secondTemp[x][0]))
        unique3.append(secondTemp[x][y])
        arraysecondTemp.append(unique3)
print "arraysecondTemp"
print arraysecondTemp

arrayunassistedTemp=[]
for x in range(0,len(unassistedTemp)):
    
    for y in range(2,len(unassistedTemp[x])):
        unique3=[]
        unique3.append(str(unassistedTemp[x][0]))
        unique3.append(unassistedTemp[x][y])
        arrayunassistedTemp.append(unique3)
print "arrayunassistedTemp"
print arrayunassistedTemp


for x in range(0,len(uniquePointsPlayers)):
    counter=0
    for y in range(0,len(unassistedGoals)):
        if uniquePointsPlayers[x]==unassistedGoals[y]:
            counter=counter+1
    uniquePointsPlayers1[x].append(counter)
    counter=0
    for y in range(0,len(FstassistedGoals)):
        if uniquePointsPlayers[x][:2]==FstassistedGoals[y]:
            counter=counter+1
            print "counter"
            print counter
    uniquePointsPlayers1[x].append(counter) 
    counter=0
    for y in range(0,len(SndassistedGoals)):
        if uniquePointsPlayers[x][:2]==SndassistedGoals[y]:
            counter=counter+1
    uniquePointsPlayers1[x].append(counter) 
    counter=0
    for y in range(0,len(onlyFstassist)):
        if uniquePointsPlayers[x][:2]==onlyFstassist[y]:
            counter=counter+1
    uniquePointsPlayers1[x].append(counter) 
    counter=0
    for y in range(0,len(SndassistedFstassist)):
        if uniquePointsPlayers[x][:2]==SndassistedFstassist[y]:
            counter=counter+1
    uniquePointsPlayers1[x].append(counter) 
    counter=0
    for y in range(0,len(newSndAssistsPlayers)):
        if uniquePointsPlayers[x][:2]==newSndAssistsPlayers[y]:
            counter=counter+1
    uniquePointsPlayers1[x].append(counter) 
    counter=0
    for y in range(0,len(arrayunassistedTemp)-1):
        if uniquePointsPlayers[x][:2]==arrayunassistedTemp[y]:
            counter=counter+1
    uniquePointsPlayers1[x].append(counter)
    counter=0
    for y in range(0,len(arrayfirstTemp)-1):
        if uniquePointsPlayers[x][:2]==arrayfirstTemp[y]:
            counter=counter+1
    uniquePointsPlayers1[x].append(counter)
    counter=0
    for y in range(0,len(arraysecondTemp)-1):
        if uniquePointsPlayers[x][:2]==arraysecondTemp[y]:
            counter=counter+1
    uniquePointsPlayers1[x].append(counter)
    
#     counter=0
#     for y in range(0,len()):
#         if uniquePointsPlayers[x]==newSndAssistsPlayers[y]:
#             counter=counter+1
#     uniquePointsPlayers1[x].append(counter) 
    
    
print "yeah"
print unassistedGoals
print uniquePointsPlayers1

# print sortedUniqueNewSndAssistsPlayers
# print "important25"
# print onlyFstassist
# print SndassistedFstassist
# print newSndAssistsPlayers
print plusMinusPlayers

# print newSndAssistsPlayers
# print Scorers
# newplusMinusPlayers=[]
# for x in range(0,len(plusMinusPlayers)):
#     newplusMinusPlayers=newplusMinusPlayers+plusMinusPlayers[x]
# print newplusMinusPlayers
# # newplusMinusPlayersWin=newplusMinusPlayers[newplusMinusPlayers[1]=='W']
# newplusMinusPlayersWin = [row for row in newplusMinusPlayers if 'W' in row[1]]
print newplusMinusPlayersWin
print FstAssistsPlayers
# temp=[]
# for x in range(0,len(newplusMinusPlayersWin)):
#     temp.append(0)
# board = []
# for i in range(3):
#     board.append([])
#     for j in range(1):
#         board[i].append(0)

# temp=newplusMinusPlayersWin[:]
# print "Scorers"
# print Scorers1
# # print Scorers2
# print Scorers3
# print temp
# print FstAssistsPlayers
# print SndAssistsPlayers
# for x in range(0,len(newplusMinusPlayersWin)):
#     print x
#     temp[x].remove(Scorers3[x][1])
#     if FstAssistsPlayers!='unassisted':
#         temp[x].remove(FstAssistsPlayers[x][1])
#         if SndAssistsPlayers!='':
#             temp[x].remove(SndAssistsPlayers[x][1])
# print temp
# print newplusMinusPlayersWin
    
# expe=newplusMinusPlayersWin-FstAssistsPlayers
# print expe
#  Scorers.append(Goal)
#             FstAssistsPlayers.append(FstAssist)
#             SndAssistsPlayers.append(SndAssist)
#             plusMinusPlayers.append(ArrayTemp)

for x in range(0,len(sortedUniqueNewScorers)):
    counter=0
    for y in range(0,len(newScorers)):
        if sortedUniqueNewScorers[x]==newScorers[y]:
            counter=counter+1
    sortedUniqueNewScorers[x].append(counter)

# print sortedUniqueNewScorers

for x in range(0,len(sortedUniqueNewFstAssistsPlayers)):
    counter=0
    for y in range(0,len(newFstAssistsPlayers)):
        if sortedUniqueNewFstAssistsPlayers[x]==newFstAssistsPlayers[y]:
            counter=counter+1
    sortedUniqueNewFstAssistsPlayers[x].append(counter)
# print sortedUniqueNewFstAssistsPlayers

for x in range(0,len(sortedUniqueNewSndAssistsPlayers)):
    counter=0
    for y in range(0,len(newSndAssistsPlayers)):
        if sortedUniqueNewSndAssistsPlayers[x]==newSndAssistsPlayers[y]:
            counter=counter+1
    sortedUniqueNewSndAssistsPlayers[x].append(counter)

20001
<td align="center">2</td>
strtemp
3
EV
20002
<td align="center">2</td>
strtemp
3
EV
20003
<td align="center">2</td>
strtemp
1
2
20004
<td align="center">2</td>
strtemp
1
2
20005
<td align="center">2</td>
strtemp
1
2
20006
<td align="center">2</td>
strtemp
1
2
20007
Even!
<td align="center">PP</td>
strtemp
3
PP
20008
<td align="center">2</td>
strtemp
SO

20009
<td align="center">2</td>
strtemp
2
PP
20010
<td align="center">2</td>
strtemp
OT
PP
20011
<td align="center">2</td>
strtemp
3
EV
20012
<td align="center">2</td>
strtemp
3
PP
20013
<td align="center">2</td>
strtemp
SO

20014
<td align="center">2</td>
strtemp
2
EV
20015
<td align="center">2</td>
strtemp
3
PP
20016
<td align="center">2</td>
strtemp
1
2
20017
<td align="center">2</td>
strtemp
1
2
20018
<td align="center">2</td>
strtemp
1
2
20019
<td align="center">2</td>
strtemp
3
PP
20020
<td align="center">2</td>
strtemp
3
EV
20021
<td align="center">2</td>
strtemp
SO

20022
<td align="center">2</td>
strtemp
1
2
20023
<td ali

IndexError: list index out of range

In [20]:
a = [1, 2, 3, 4]
# a.remove(2)
# print a
print dict((el,0) for el in a)
print set('aaabcabccd')
print a
# a=a.remove(2)
a.remove(2)
print a
a.append(5)
print a
print a[:len(a)]


from random import randint

class Node:
    def __init__(self, value):
        self.value = value
        self.next = None

    def __str__(self):
        return str(self.value)

class LinkedList:
    def __init__(self):
        self.head = None
        self.tail = None

    def addNode(self,value):
        node = Node(value)
        #if the old list is none, set new node as the first node
        if self.head == None:
            self.head = node
            self.tail = node
        else:
            self.tail.next = node
            self.tail = node

    def __str__(self):
        if self.head != None:
            index = self.head
            nodestore = [str(index.value)]
            while index.next != None:
                index = index.next
                nodestore.append(str(index.value))
            return "LinkedList  [ " + "->".join(nodestore) + " ]"
        return "LinkedList  []"


    #remove the first node that have the same value as the given node_value
    def removeNode(self, node_value):
        current = self.head
        if current.value == node_value:
            self.head = self.head.next
        while(current.next != None):
            if current.next.value == node_value:
                current.next = current.next.next
                break
            else:
                current = current.next


def randomLinkedList(length, min, max):
    linkedlist = LinkedList()
    for i in range(length):
        value = randint(min, max)
        linkedlist.addNode(value)
    return linkedlist
# from LinkedList import *


# use a hash table, O(n)
def deleteDups(linkedlist):
    if (linkedlist.head != None):
        currNode = linkedlist.head
        dic =  {currNode.value: True}
        while currNode.next != None:
            if currNode.next.value in dic:
                currNode.next = currNode.next.next
            else:
                dic[currNode.next.value] = True
                currNode = currNode.next


# use no data structure, O(n2)
def deleteDups2(linkedlist):
    currNode = linkedlist.head
    while currNode != None:
        runner = currNode
        while runner.next != None:
            if runner.next.value == currNode.value:
                runner.next = runner.next.next
            else:
                runner = runner.next
        currNode = currNode.next




#---------------- test --------------------
L1 = randomLinkedList(9, 3, 7)
print L1
deleteDups(L1)
print L1
print
L2 = randomLinkedList(9, 3, 7)
print L2
deleteDups2(L2)
print L2

{1: 0, 2: 0, 3: 0, 4: 0}
set(['a', 'c', 'b', 'd'])
[1, 2, 3, 4]
[1, 3, 4]
[1, 3, 4, 5]
[1, 3, 4, 5]
LinkedList  [ 6->3->7->5->7->7->5->7->7 ]
LinkedList  [ 6->3->7->5 ]

LinkedList  [ 4->6->6->7->5->3->5->6->7 ]
LinkedList  [ 4->6->7->5->3 ]


In [31]:
class Queue:
    def __init__(self):
        self.items = []

    def isEmpty(self):
        return self.items == []

    def enqueue(self, item):
        self.items.insert(0,item)

    def dequeue(self):
        return self.items.pop()

    def size(self):
        return len(self.items)
    
q=Queue()

q.enqueue(4)
q.enqueue('dog')
q.enqueue(True)
# print(q.size())
# print q.dequeue()
# print q.dequeue()


# Approach 1. Use a tuple to store data and min in every stack element
class StackWithMin(object):
	def __init__(self, storage = []):
		self.storage = storage
	def empty(self):
		return len(self.storage) == 0
	def push(self, value):
		if len(self.storage) == 0 or value < self.storage[-1][1]:
			self.storage.append((value, value))
# 			print self.storage
		else:
			self.storage.append((value, self.storage[-1][1]))
	def pop(self):
		return self.storage.pop()[0]
	def get_top(self):
		if len(self.storage) == 0: return None
		return self.storage[-1][0]
	def get_min(self):
		if len(self.storage) == 0: return None
		return self.storage[-1][1]

from random import randrange
S1 = StackWithMin()
# S2 = StackWithMin2()
test_list = [randrange(100) for x in xrange(10)]
for num in test_list:
	S1.push(num)
# 	S2.push(num)
	print num, 
print ""


[(28, 28)]
28 [(28, 28), (5, 5)]
5 85 66 43 [(28, 28), (5, 5), (85, 5), (66, 5), (43, 5), (1, 1)]
1 20 61 77 88 


In [34]:
class AnimalQueue(object):
	def __init__(self):
		from collections import deque
		self.dog_q = deque()
		self.cat_q = deque()
		self.time_stamp = 0
# AnimalQueue()

In [38]:
class SetOfStacks:
    
    def __init__(self,capacity):
        self.capacity = capacity
        self.stacks = []

    def push(self, value):
        if (len(self.stacks) == 0) or (len(self.stacks[-1]) == self.capacity):
            self.stacks.append([])
        self.stacks[-1].append(value)

    def pop(self):
        if len(self.stacks) == 0:
            return None
        data = self.stacks[-1].pop()
        if len(self.stacks[-1]) == 0:
            self.stacks.pop()
        return data
    
    # Pop operation on a specifit sub-stack. (Index begins with 1)
    # Not "rolling over" version. OK with some stacks not at full capacity
    def popAt(self, index):
        if index < 1 or index > len(self.stacks) or len(self.stacks[index-1]) == 0:
            return None
        else:
            return self.stacks[index-1].pop() 



#-----------------test-------------------
def test():
    setofstacks = SetOfStacks(8)
    for i in range(24):
        setofstacks.push(i)
        print i,
    print ""

    for i in range(5):
        print "Popped", setofstacks.pop()

    print "Test for popAt"
    for i in range(5):
        for i in range(3):
            print "Popped", setofstacks.popAt(i+1)


if __name__ == "__main__":
    test()

0 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 
Popped 23
Popped 22
Popped 21
Popped 20
Popped 19
Test for popAt
Popped 7
Popped 15
Popped 18
Popped 6
Popped 14
Popped 17
Popped 5
Popped 13
Popped 16
Popped 4
Popped 12
Popped None
Popped 3
Popped 11
Popped None


In [45]:
#binary tree python
class BinaryTree:
    def __init__(self, content, left = None, right = None):
        self.content = content
        self.left = left
        self.right = right

    def __str__(self):
        return "( " + str(self.content) + " ( " + str(self.left) + " | " + str(self.right) + "))" 

#Given a sorted (increasing order) array with unique integer elements, write an
#algorithm to create a binary search tree with minimal height.


def int_array_to_binary_search_tree(intarray):
    #use the middle of the array to divide it. this ensures minimal height.
    if len(intarray) == 0:
        return None
    if len(intarray) == 1:
        return BinaryTree(intarray[0])
    cut = len(intarray) / 2
    return BinaryTree( intarray[cut],\
                      int_array_to_binary_search_tree(intarray[0:cut]), int_array_to_binary_search_tree(intarray[cut+1:]))

#testing

intarray1=[1,2,3,4,5,6,7,8,9,10,12,15,18,22,43,144,515]
intarray2=[1,2,3,4,5,6,7,8,9,10,12,15,18,22,43,144,515,4123]

print str(int_array_to_binary_search_tree(intarray1))

print str(int_array_to_binary_search_tree(intarray2))

( 9 ( ( 5 ( ( 3 ( ( 2 ( ( 1 ( None | None)) | None)) | ( 4 ( None | None)))) | ( 7 ( ( 6 ( None | None)) | ( 8 ( None | None)))))) | ( 22 ( ( 15 ( ( 12 ( ( 10 ( None | None)) | None)) | ( 18 ( None | None)))) | ( 144 ( ( 43 ( None | None)) | ( 515 ( None | None))))))))
( 10 ( ( 5 ( ( 3 ( ( 2 ( ( 1 ( None | None)) | None)) | ( 4 ( None | None)))) | ( 8 ( ( 7 ( ( 6 ( None | None)) | None)) | ( 9 ( None | None)))))) | ( 43 ( ( 18 ( ( 15 ( ( 12 ( None | None)) | None)) | ( 22 ( None | None)))) | ( 515 ( ( 144 ( None | None)) | ( 4123 ( None | None))))))))


In [48]:
class BinaryTreeNode:

    def __init__(self, value):
        self.value = value
        self.left = None
        self.right = None
        self.parent = None

    def setLeft(self, leftvalue):
        leftnode = BinaryTreeNode(leftvalue)
        self.left = leftnode
        if leftnode != None:
            leftnode.parent = self

    def setRight(self, rightvalue):
        rightnode = BinaryTreeNode(rightvalue)
        self.right = rightnode
        if rightnode != None:
            rightnode.parent = self


def findSum(node, givenSum, path=None, depth=0):
    if node is None:
        return
    if path is None:
        path = []
    if len(path) > depth:
        path[depth] = node.value
    else:
        path.append(node.value)
    print path
    print depth
    # Look up to see if there are paths end up with this node and sum to the given value
    temp = 0
    for i in range(depth, -1, -1):
        temp += path[i]
        if temp == givenSum:
            printPath(path, i, depth)
    
    findSum(node.left, givenSum, path, depth+1)
    findSum(node.right, givenSum, path, depth+1)


def printPath(path, start, end):
    for i in range(start, end + 1):
        print path[i],
    print ""




# --------------test----------------
#               1
#              / \
#             2   3
#            / \ / \
#           4  5 3  4 
#             /
#            7
# Sum = 7
# Path:
# 1 2 4
# 2 5
# 7
# 1 3 3
# 3 4

def main():
    givenSum = 7
    root = BinaryTreeNode(1)
    root.setLeft(2)
    root.setRight(3)
    root.left.setLeft(4)
    root.left.setRight(5)
    root.right.setLeft(3)
    root.right.setRight(4)
    root.left.right.setLeft(7)

    findSum(root, givenSum)


if __name__ == "__main__":
    main()

[1]
0
[1, 2]
1
[1, 2, 4]
2
1 2 4 
[1, 2, 5]
2
2 5 
[1, 2, 5, 7]
3
7 
[1, 3, 5, 7]
1
[1, 3, 3, 7]
2
1 3 3 
[1, 3, 4, 7]
2
3 4 
